In [1]:
nb_epochs = 2000

In [2]:
#ResN-1
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('relu')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('relu')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('relu')(conv_z)
     
    shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
  # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
    
  # shortcut_y = x #keras.layers.BatchNormalization()(x)
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_z])
    y = keras.layers.Activation('relu')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist1 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log1 = pd.DataFrame(hist1.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering 
res_model1 = keras.models.load_model(model_h5_file)


A module that was compiled using NumPy 1.x cannot be run in
NumPy 2.0.2 as it may crash. To support both 1.x and 2.x
versions of NumPy, modules must be compiled with NumPy 2.0.
Some module may need to rebuild instead e.g. with 'pybind11>=2.12'.

If you are a user of the module, the easiest solution will be to
downgrade to 'numpy<2' or try to upgrade the affected module.
We expect that some modules will need time to support NumPy 2.

Traceback (most recent call last):  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 197, in _run_module_as_main
    return _run_code(code, main_globals, None,
  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 87, in _run_code
    exec(code, run_globals)
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "C:\Users\KJH\anaconda3\lib\site-packages\traitlets\config\application.py", line 846, in launch_instance
    app.start()
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipyke

AttributeError: _ARRAY_API not found


A module that was compiled using NumPy 1.x cannot be run in
NumPy 2.0.2 as it may crash. To support both 1.x and 2.x
versions of NumPy, modules must be compiled with NumPy 2.0.
Some module may need to rebuild instead e.g. with 'pybind11>=2.12'.

If you are a user of the module, the easiest solution will be to
downgrade to 'numpy<2' or try to upgrade the affected module.
We expect that some modules will need time to support NumPy 2.

Traceback (most recent call last):  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 197, in _run_module_as_main
    return _run_code(code, main_globals, None,
  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 87, in _run_code
    exec(code, run_globals)
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "C:\Users\KJH\anaconda3\lib\site-packages\traitlets\config\application.py", line 846, in launch_instance
    app.start()
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipyke

AttributeError: _ARRAY_API not found


A module that was compiled using NumPy 1.x cannot be run in
NumPy 2.0.2 as it may crash. To support both 1.x and 2.x
versions of NumPy, modules must be compiled with NumPy 2.0.
Some module may need to rebuild instead e.g. with 'pybind11>=2.12'.

If you are a user of the module, the easiest solution will be to
downgrade to 'numpy<2' or try to upgrade the affected module.
We expect that some modules will need time to support NumPy 2.

Traceback (most recent call last):  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 197, in _run_module_as_main
    return _run_code(code, main_globals, None,
  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 87, in _run_code
    exec(code, run_globals)
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "C:\Users\KJH\anaconda3\lib\site-packages\traitlets\config\application.py", line 846, in launch_instance
    app.start()
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipyke

...

Epoch 1793/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.9999 - loss: 0.0083 - val_accuracy: 0.4715 - val_loss: 96.9648 - learning_rate: 1.2500e-04
Epoch 1794/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0092 - val_accuracy: 0.4666 - val_loss: 99.3784 - learning_rate: 1.2500e-04
Epoch 1795/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.9994 - loss: 0.0107 - val_accuracy: 0.4649 - val_loss: 98.0852 - learning_rate: 1.2500e-04
Epoch 1796/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0100 - val_accuracy: 0.4649 - val_loss: 99.9234 - learning_rate: 1.2500e-04
Epoch 1797/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0126 - val_accuracy: 0.4731 - val_loss: 97.0033 - learning_rate: 1.2500e-04
Epoch 1798/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0103 - val_accuracy: 0.4649 - val_loss: 99.8342 - learning_rate: 1.2500e-04
Epoch 1799/2000
37/37 ━━━━━━━━━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0103 - val_accuracy: 0.4731 - val_loss: 96.2641 - learning_rate: 1.2500e-04
Epoch 1836/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0087 - val_accuracy: 0.4731 - val_loss: 96.7177 - learning_rate: 1.2500e-04
Epoch 1837/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0119 - val_accuracy: 0.4715 - val_loss: 97.7215 - learning_rate: 1.2500e-04
Epoch 1838/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0087 - val_accuracy: 0.4731 - val_loss: 97.1675 - learning_rate: 1.2500e-04
Epoch 1839/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0105 - val_accuracy: 0.4747 - val_loss: 94.7803 - learning_rate: 1.2500e-04
Epoch 1840/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.9977 - loss: 0.0103 - val_accuracy: 0.4747 - val_loss: 95.0629 - learning_rate: 1.2500e-04
Epoch 1841/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0097 - val_accuracy: 0.4780 - val_loss: 89.6877 - learning_rate: 1.2500e-04
Epoch 1878/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 1.0000 - loss: 0.0098 - val_accuracy: 0.4763 - val_loss: 93.6177 - learning_rate: 1.2500e-04
Epoch 1879/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0073 - val_accuracy: 0.4747 - val_loss: 94.2670 - learning_rate: 1.2500e-04
Epoch 1880/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0075 - val_accuracy: 0.4715 - val_loss: 91.6481 - learning_rate: 1.2500e-04
Epoch 1881/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0087 - val_accuracy: 0.4747 - val_loss: 96.2858 - learning_rate: 1.2500e-04
Epoch 1882/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 0.0099 - val_accuracy: 0.4878 - val_loss: 88.3568 - learning_rate: 1.2500e-04
Epoch 1883/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0094 - val_accuracy: 0.4747 - val_loss: 92.2585 - learning_rate: 1.2500e-04
Epoch 1920/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0084 - val_accuracy: 0.4845 - val_loss: 89.7062 - learning_rate: 1.2500e-04
Epoch 1921/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0071 - val_accuracy: 0.4812 - val_loss: 91.3712 - learning_rate: 1.2500e-04
Epoch 1922/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 0.0105 - val_accuracy: 0.4845 - val_loss: 90.5850 - learning_rate: 1.2500e-04
Epoch 1923/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0095 - val_accuracy: 0.4829 - val_loss: 90.2666 - learning_rate: 1.2500e-04
Epoch 1924/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0079 - val_accuracy: 0.4861 - val_loss: 88.0638 - learning_rate: 1.2500e-04
Epoch 1925/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0074 - val_accuracy: 0.4845 - val_loss: 90.7584 - learning_rate: 1.2500e-04
Epoch 1962/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0074 - val_accuracy: 0.4910 - val_loss: 84.9438 - learning_rate: 1.2500e-04
Epoch 1963/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0069 - val_accuracy: 0.4894 - val_loss: 90.1368 - learning_rate: 1.2500e-04
Epoch 1964/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 0.0083 - val_accuracy: 0.4878 - val_loss: 87.0000 - learning_rate: 1.2500e-04
Epoch 1965/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0079 - val_accuracy: 0.4878 - val_loss: 87.9370 - learning_rate: 1.2500e-04
Epoch 1966/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0067 - val_accuracy: 0.4845 - val_loss: 89.7146 - learning_rate: 1.2500e-04
Epoch 1967/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms

In [3]:
#ResN-2
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('relu')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('relu')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('relu')(conv_z)
    
    print ('build conv_w')
    conv_w = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_z)
    conv_w = keras.layers.Activation('relu')(conv_w)
     
    shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
  # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
    
  # shortcut_y = x #keras.layers.BatchNormalization()(x)
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_w])
    y = keras.layers.Activation('relu')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist2 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log2 = pd.DataFrame(hist2.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering 
res_model2 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
build conv_w
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 7s 40ms/step - accuracy: 0.5182 - loss: 0.6935 - val_accuracy: 0.6199 - val_loss: 1.1963 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.5559 - loss: 0.6886 - val_accuracy: 0.6199 - val_loss: 0.9621 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.5940 - loss: 0.6767 - val_accuracy: 0.6199 - val_loss: 1.0306 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5458 - loss: 0.6884 - val_accuracy: 0.6199 - val_loss: 1.0032 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.5501 - loss: 0.6887 - val_accuracy: 0.6199 - val_loss: 0.9852 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5770 - loss: 0.6832 - val_accuracy: 0.6199 - val_loss: 1.2776 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7554 - loss: 0.5285 - val_accuracy: 0.6835 - val_loss: 0.7291 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6873 - loss: 0.5838 - val_accuracy: 0.5318 - val_loss: 1.2020 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7032 - loss: 0.5633 - val_accuracy: 0.6476 - val_loss: 1.2936 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7212 - loss: 0.5477 - val_accuracy: 0.6036 - val_loss: 0.9114 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6892 - loss: 0.5849 - val_accuracy: 0.6623 - val_loss: 1.0413 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7134 - loss: 0.5739 - val_accuracy: 0.5351 - val_loss: 1.3022 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6878 - loss: 0.5823 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7435 - loss: 0.5188 - val_accuracy: 0.4454 - val_loss: 4.1848 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7345 - loss: 0.5051 - val_accuracy: 0.5449 - val_loss: 2.9555 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7784 - loss: 0.4828 - val_accuracy: 0.4323 - val_loss: 5.5229 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7619 - loss: 0.4723 - val_accuracy: 0.5220 - val_loss: 2.9635 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7651 - loss: 0.4808 - val_accuracy: 0.5204 - val_loss: 3.1993 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7575 - loss: 0.4968 - val_accuracy: 0.5367 - val_loss: 3.3997 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7621 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.8014 - loss: 0.3847 - val_accuracy: 0.4029 - val_loss: 13.6509 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7948 - loss: 0.3929 - val_accuracy: 0.3883 - val_loss: 15.6818 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.8207 - loss: 0.3825 - val_accuracy: 0.4013 - val_loss: 16.7982 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.8163 - loss: 0.3714 - val_accuracy: 0.4633 - val_loss: 7.0465 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.8417 - loss: 0.3464 - val_accuracy: 0.3964 - val_loss: 14.6159 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.8194 - loss: 0.3574 - val_accuracy: 0.4013 - val_loss: 13.0884 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.8320 - loss

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.8811 - loss: 0.2657 - val_accuracy: 0.4192 - val_loss: 23.4630 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.8824 - loss: 0.2731 - val_accuracy: 0.4209 - val_loss: 30.2296 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.8909 - loss: 0.2489 - val_accuracy: 0.4176 - val_loss: 30.1363 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.8846 - loss: 0.2594 - val_accuracy: 0.4372 - val_loss: 21.1953 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.8943 - loss: 0.2564 - val_accuracy: 0.4470 - val_loss: 22.8920 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.8693 - loss: 0.2606 - val_accuracy: 0.4176 - val_loss: 37.7584 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.8893 - los

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 1.0000 - loss: 5.4005e-06 - val_accuracy: 0.4388 - val_loss: 137.5954 - learning_rate: 1.0000e-04
Epoch 1836/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 5.9928e-06 - val_accuracy: 0.4388 - val_loss: 137.6043 - learning_rate: 1.0000e-04
Epoch 1837/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 5.0235e-06 - val_accuracy: 0.4388 - val_loss: 137.7059 - learning_rate: 1.0000e-04
Epoch 1838/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 1.0000 - loss: 3.1679e-06 - val_accuracy: 0.4388 - val_loss: 137.6871 - learning_rate: 1.0000e-04
Epoch 1839/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 3.6408e-06 - val_accuracy: 0.4388 - val_loss: 137.7273 - learning_rate: 1.0000e-04
Epoch 1840/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 2.8753e-06 - val_accuracy: 0.4388 - val_loss: 137.7281 - learning_rate: 1.0000e-04
Epoch 1841/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 2.1221e-06 - val_accuracy: 0.4388 - val_loss: 137.8963 - learning_rate: 1.0000e-04
Epoch 1877/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 1.5850e-06 - val_accuracy: 0.4388 - val_loss: 137.8526 - learning_rate: 1.0000e-04
Epoch 1878/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 1.0000 - loss: 2.0801e-06 - val_accuracy: 0.4388 - val_loss: 137.8627 - learning_rate: 1.0000e-04
Epoch 1879/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 1.0000 - loss: 3.6189e-06 - val_accuracy: 0.4388 - val_loss: 137.8139 - learning_rate: 1.0000e-04
Epoch 1880/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 2.2146e-06 - val_accuracy: 0.4388 - val_loss: 137.8173 - learning_rate: 1.0000e-04
Epoch 1881/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 2.7955e-06 - val_accuracy: 0.4388 - val_loss: 137.8127 - learning_rate: 1.0000e-04
Epoch 1882/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 2.2821e-06 - val_accuracy: 0.4388 - val_loss: 136.8474 - learning_rate: 1.0000e-04
Epoch 1918/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 2.3710e-06 - val_accuracy: 0.4388 - val_loss: 136.8672 - learning_rate: 1.0000e-04
Epoch 1919/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 1.1452e-06 - val_accuracy: 0.4388 - val_loss: 136.9074 - learning_rate: 1.0000e-04
Epoch 1920/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 1.3324e-06 - val_accuracy: 0.4388 - val_loss: 136.6927 - learning_rate: 1.0000e-04
Epoch 1921/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 1.8604e-06 - val_accuracy: 0.4388 - val_loss: 136.7275 - learning_rate: 1.0000e-04
Epoch 1922/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 1.3246e-06 - val_accuracy: 0.4388 - val_loss: 136.7026 - learning_rate: 1.0000e-04
Epoch 1923/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 1.1362e-06 - val_accuracy: 0.4372 - val_loss: 135.8708 - learning_rate: 1.0000e-04
Epoch 1959/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 1.3058e-06 - val_accuracy: 0.4372 - val_loss: 135.9244 - learning_rate: 1.0000e-04
Epoch 1960/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 7.7435e-07 - val_accuracy: 0.4372 - val_loss: 135.7681 - learning_rate: 1.0000e-04
Epoch 1961/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 1.1065e-06 - val_accuracy: 0.4372 - val_loss: 135.8328 - learning_rate: 1.0000e-04
Epoch 1962/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 1.0233e-06 - val_accuracy: 0.4372 - val_loss: 135.8121 - learning_rate: 1.0000e-04
Epoch 1963/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 1.0898e-06 - val_accuracy: 0.4372 - val_loss: 135.4587 - learning_rate: 1.0000e-04
Epoch 1964/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 6.0042e-07 - val_accuracy: 0.4388 - val_loss: 134.3296 - learning_rate: 1.0000e-04
Epoch 2000/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 6.4876e-07 - val_accuracy: 0.4388 - val_loss: 134.4209 - learning_rate: 1.0000e-04


In [4]:
#ResN-3
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('relu')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('relu')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('relu')(conv_z)
     
    shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
    shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
  # shortcut_y = keras.layers.BatchNormalization()(x)  
  # shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_z])
    y = keras.layers.Activation('relu')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist3 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log3 = pd.DataFrame(hist3.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering res_modle3
res_model3 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 9s 46ms/step - accuracy: 0.5294 - loss: 0.7838 - val_accuracy: 0.6199 - val_loss: 0.6728 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.4760 - loss: 0.7069 - val_accuracy: 0.6199 - val_loss: 0.7674 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5998 - loss: 0.6905 - val_accuracy: 0.6199 - val_loss: 0.8130 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.5496 - loss: 0.6984 - val_accuracy: 0.6199 - val_loss: 0.6734 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.5482 - loss: 0.6911 - val_accuracy: 0.6199 - val_loss: 0.6842 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.5487 - loss: 0.6850 - val_accuracy: 0.6199 - val_loss: 1.2211 - learning_rate

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6914 - loss: 0.5612 - val_accuracy: 0.6819 - val_loss: 0.7657 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6864 - loss: 0.5892 - val_accuracy: 0.6509 - val_loss: 1.1537 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7221 - loss: 0.5587 - val_accuracy: 0.4225 - val_loss: 1.8975 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6738 - loss: 0.5768 - val_accuracy: 0.3866 - val_loss: 3.4743 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7142 - loss: 0.5850 - val_accuracy: 0.4600 - val_loss: 1.4038 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6651 - loss: 0.6040 - val_accuracy: 0.6509 - val_loss: 1.2834 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7008 - loss: 0.5901 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7037 - loss: 0.5551 - val_accuracy: 0.6525 - val_loss: 1.7253 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7045 - loss: 0.5521 - val_accuracy: 0.6346 - val_loss: 2.5915 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7348 - loss: 0.5288 - val_accuracy: 0.6591 - val_loss: 1.1712 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7044 - loss: 0.5643 - val_accuracy: 0.6427 - val_loss: 2.5259 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7322 - loss: 0.5317 - val_accuracy: 0.5351 - val_loss: 1.5882 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6789 - loss: 0.5797 - val_accuracy: 0.6411 - val_loss: 2.4223 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6902 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7206 - loss: 0.5508 - val_accuracy: 0.7113 - val_loss: 1.0914 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7006 - loss: 0.5580 - val_accuracy: 0.6656 - val_loss: 1.7586 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6773 - loss: 0.5613 - val_accuracy: 0.6884 - val_loss: 0.8673 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7101 - loss: 0.5744 - val_accuracy: 0.5383 - val_loss: 2.2947 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7332 - loss: 0.5373 - val_accuracy: 0.6982 - val_loss: 1.0751 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7155 - loss: 0.5413 - val_accuracy: 0.6330 - val_loss: 4.1150 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7212 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7330 - loss: 0.5139 - val_accuracy: 0.5628 - val_loss: 2.4026 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7195 - loss: 0.5327 - val_accuracy: 0.5220 - val_loss: 3.2476 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7533 - loss: 0.5038 - val_accuracy: 0.4600 - val_loss: 5.3955 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7520 - loss: 0.5278 - val_accuracy: 0.6085 - val_loss: 2.0982 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7764 - loss: 0.4780 - val_accuracy: 0.6803 - val_loss: 1.0641 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7116 - loss: 0.5245 - val_accuracy: 0.4078 - val_loss: 6.0519 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7138 - loss: 0.5

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 0.0017 - val_accuracy: 0.5073 - val_loss: 39.0725 - learning_rate: 2.5000e-04
Epoch 1797/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 0.0017 - val_accuracy: 0.5024 - val_loss: 40.6933 - learning_rate: 2.5000e-04
Epoch 1798/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 0.0020 - val_accuracy: 0.5073 - val_loss: 40.3492 - learning_rate: 2.5000e-04
Epoch 1799/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0019 - val_accuracy: 0.4976 - val_loss: 41.2788 - learning_rate: 2.5000e-04
Epoch 1800/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.5057 - val_loss: 40.5113 - learning_rate: 2.5000e-04
Epoch 1801/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 0.0018 - val_accuracy: 0.5073 - val_loss: 40.1262 - learning_rate: 1.2500e-04
Epoch 1802/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 1.0000 - loss: 0.0011 - val_accuracy: 0.5008 - val_loss: 41.2281 - learning_rate: 1.2500e-04
Epoch 1839/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0017 - val_accuracy: 0.5024 - val_loss: 41.2332 - learning_rate: 1.2500e-04
Epoch 1840/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 0.0018 - val_accuracy: 0.5041 - val_loss: 40.3239 - learning_rate: 1.2500e-04
Epoch 1841/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 0.0013 - val_accuracy: 0.5041 - val_loss: 41.3051 - learning_rate: 1.2500e-04
Epoch 1842/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.5024 - val_loss: 41.0576 - learning_rate: 1.2500e-04
Epoch 1843/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4976 - val_loss: 41.7809 - learning_rate: 1.2500e-04
Epoch 1844/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 0.0023 - val_accuracy: 0.5057 - val_loss: 39.0919 - learning_rate: 1.2500e-04
Epoch 1881/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0019 - val_accuracy: 0.4878 - val_loss: 44.6376 - learning_rate: 1.2500e-04
Epoch 1882/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0013 - val_accuracy: 0.4927 - val_loss: 42.3020 - learning_rate: 1.2500e-04
Epoch 1883/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4927 - val_loss: 42.0302 - learning_rate: 1.2500e-04
Epoch 1884/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 0.0016 - val_accuracy: 0.4943 - val_loss: 42.6133 - learning_rate: 1.2500e-04
Epoch 1885/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0014 - val_accuracy: 0.4976 - val_loss: 42.0625 - learning_rate: 1.2500e-04
Epoch 1886/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 0.0010 - val_accuracy: 0.4910 - val_loss: 42.0307 - learning_rate: 1.2500e-04
Epoch 1923/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0011 - val_accuracy: 0.4943 - val_loss: 43.0527 - learning_rate: 1.2500e-04
Epoch 1924/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 0.0014 - val_accuracy: 0.4927 - val_loss: 42.0096 - learning_rate: 1.2500e-04
Epoch 1925/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 0.0014 - val_accuracy: 0.4927 - val_loss: 43.3146 - learning_rate: 1.2500e-04
Epoch 1926/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4943 - val_loss: 41.7894 - learning_rate: 1.2500e-04
Epoch 1927/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 0.0017 - val_accuracy: 0.4943 - val_loss: 42.2205 - learning_rate: 1.2500e-04
Epoch 1928/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 29ms/step - accuracy: 1.0000 - loss: 9.4672e-04 - val_accuracy: 0.4959 - val_loss: 40.1789 - learning_rate: 1.2500e-04
Epoch 1965/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 0.0014 - val_accuracy: 0.4959 - val_loss: 40.7548 - learning_rate: 1.2500e-04
Epoch 1966/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 0.0013 - val_accuracy: 0.4943 - val_loss: 42.4921 - learning_rate: 1.2500e-04
Epoch 1967/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4959 - val_loss: 40.7305 - learning_rate: 1.2500e-04
Epoch 1968/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 0.0011 - val_accuracy: 0.4992 - val_loss: 40.1619 - learning_rate: 1.2500e-04
Epoch 1969/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4976 - val_loss: 41.2642 - learning_rate: 1.2500e-04
Epoch 1970/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 

In [5]:
#ResN-4
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('relu')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('relu')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('relu')(conv_z)
    
    print ('build conv_w')
    conv_w = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_z)
    conv_w = keras.layers.Activation('relu')(conv_w)
     
    shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
    shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
  # shortcut_y = keras.layers.BatchNormalization()(x)  
  # shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_w])
    y = keras.layers.Activation('relu')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist4 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log4 = pd.DataFrame(hist4.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model4 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
build conv_w
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 10s 51ms/step - accuracy: 0.5346 - loss: 0.7810 - val_accuracy: 0.6199 - val_loss: 0.8130 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 39ms/step - accuracy: 0.5816 - loss: 0.6899 - val_accuracy: 0.6199 - val_loss: 0.6693 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.5732 - loss: 0.6869 - val_accuracy: 0.6199 - val_loss: 0.6762 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.5056 - loss: 0.7006 - val_accuracy: 0.6199 - val_loss: 0.7776 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.5585 - loss: 0.6835 - val_accuracy: 0.3931 - val_loss: 0.7837 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 42ms/step - accuracy: 0.5626 - loss: 0.6883 - val_accuracy: 0.4470 - val_loss: 0.7450 -

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6814 - loss: 0.5929 - val_accuracy: 0.6248 - val_loss: 3.4135 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6586 - loss: 0.6035 - val_accuracy: 0.6558 - val_loss: 1.1419 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7376 - loss: 0.5328 - val_accuracy: 0.6362 - val_loss: 1.8776 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 41ms/step - accuracy: 0.7054 - loss: 0.5811 - val_accuracy: 0.6754 - val_loss: 0.9091 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7190 - loss: 0.5643 - val_accuracy: 0.6346 - val_loss: 2.2539 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7512 - loss: 0.5371 - val_accuracy: 0.7015 - val_loss: 0.7691 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7495 - loss: 0.5476 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7485 - loss: 0.5361 - val_accuracy: 0.6346 - val_loss: 3.1559 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7272 - loss: 0.5263 - val_accuracy: 0.6378 - val_loss: 3.1158 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7259 - loss: 0.5143 - val_accuracy: 0.5481 - val_loss: 1.4611 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7439 - loss: 0.4975 - val_accuracy: 0.6444 - val_loss: 2.5859 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7651 - loss: 0.5058 - val_accuracy: 0.6591 - val_loss: 0.8735 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7578 - loss: 0.5249 - val_accuracy: 0.6949 - val_loss: 1.1953 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7223 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7951 - loss: 0.4429 - val_accuracy: 0.4062 - val_loss: 4.6067 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7581 - loss: 0.4447 - val_accuracy: 0.5122 - val_loss: 1.1687 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7906 - loss: 0.4351 - val_accuracy: 0.6819 - val_loss: 0.6610 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7647 - loss: 0.4720 - val_accuracy: 0.7064 - val_loss: 0.9549 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 41ms/step - accuracy: 0.7931 - loss: 0.4717 - val_accuracy: 0.6623 - val_loss: 1.2301 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7918 - loss: 0.4354 - val_accuracy: 0.4829 - val_loss: 3.2650 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.8085 - loss: 0.4

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.8351 - loss: 0.3375 - val_accuracy: 0.4323 - val_loss: 9.3136 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.8276 - loss: 0.3703 - val_accuracy: 0.6819 - val_loss: 1.6729 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.8182 - loss: 0.3855 - val_accuracy: 0.4046 - val_loss: 6.9778 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.8108 - loss: 0.3977 - val_accuracy: 0.4258 - val_loss: 9.0017 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.8187 - loss: 0.3679 - val_accuracy: 0.4763 - val_loss: 7.6463 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.8462 - loss: 0.3521 - val_accuracy: 0.4682 - val_loss: 8.6556 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.8388 - loss: 0.3

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 2.1017e-06 - val_accuracy: 0.4698 - val_loss: 32.5219 - learning_rate: 1.0000e-04
Epoch 1800/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 2.4456e-06 - val_accuracy: 0.4698 - val_loss: 32.5847 - learning_rate: 1.0000e-04
Epoch 1801/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 2.3312e-06 - val_accuracy: 0.4698 - val_loss: 32.5497 - learning_rate: 1.0000e-04
Epoch 1802/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 2.6795e-06 - val_accuracy: 0.4698 - val_loss: 32.7317 - learning_rate: 1.0000e-04
Epoch 1803/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 2.6036e-06 - val_accuracy: 0.4698 - val_loss: 32.4973 - learning_rate: 1.0000e-04
Epoch 1804/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 2.8880e-06 - val_accuracy: 0.4715 - val_loss: 32.3395 - learning_rate: 1.0000e-04
Epoch 1805/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 1.9729e-06 - val_accuracy: 0.4731 - val_loss: 31.6003 - learning_rate: 1.0000e-04
Epoch 1841/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 1.5160e-06 - val_accuracy: 0.4731 - val_loss: 31.6292 - learning_rate: 1.0000e-04
Epoch 1842/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 2.1213e-06 - val_accuracy: 0.4731 - val_loss: 31.6948 - learning_rate: 1.0000e-04
Epoch 1843/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 1.3064e-06 - val_accuracy: 0.4731 - val_loss: 31.4525 - learning_rate: 1.0000e-04
Epoch 1844/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 1.5289e-06 - val_accuracy: 0.4731 - val_loss: 31.2891 - learning_rate: 1.0000e-04
Epoch 1845/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 1.6100e-06 - val_accuracy: 0.4731 - val_loss: 31.3899 - learning_rate: 1.0000e-04
Epoch 1846/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 1.0206e-06 - val_accuracy: 0.4731 - val_loss: 31.4502 - learning_rate: 1.0000e-04
Epoch 1882/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 1.4483e-06 - val_accuracy: 0.4731 - val_loss: 31.2866 - learning_rate: 1.0000e-04
Epoch 1883/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 1.3881e-06 - val_accuracy: 0.4731 - val_loss: 31.7910 - learning_rate: 1.0000e-04
Epoch 1884/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 1.5204e-06 - val_accuracy: 0.4731 - val_loss: 31.4559 - learning_rate: 1.0000e-04
Epoch 1885/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 1.2410e-06 - val_accuracy: 0.4731 - val_loss: 31.7721 - learning_rate: 1.0000e-04
Epoch 1886/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 1.1360e-06 - val_accuracy: 0.4715 - val_loss: 31.6737 - learning_rate: 1.0000e-04
Epoch 1887/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 7.6988e-04 - val_accuracy: 0.5008 - val_loss: 28.1877 - learning_rate: 1.0000e-04
Epoch 1923/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 8.8628e-05 - val_accuracy: 0.5008 - val_loss: 27.7732 - learning_rate: 1.0000e-04
Epoch 1924/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 3.2379e-05 - val_accuracy: 0.4976 - val_loss: 27.8850 - learning_rate: 1.0000e-04
Epoch 1925/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 4.0957e-05 - val_accuracy: 0.4976 - val_loss: 27.9632 - learning_rate: 1.0000e-04
Epoch 1926/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 2.3007e-05 - val_accuracy: 0.4959 - val_loss: 28.0283 - learning_rate: 1.0000e-04
Epoch 1927/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 6.5463e-05 - val_accuracy: 0.4943 - val_loss: 28.0900 - learning_rate: 1.0000e-04
Epoch 1928/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 8.3186e-06 - val_accuracy: 0.4959 - val_loss: 26.7448 - learning_rate: 1.0000e-04
Epoch 1964/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 1.0080e-05 - val_accuracy: 0.4959 - val_loss: 26.6788 - learning_rate: 1.0000e-04
Epoch 1965/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 4.6388e-06 - val_accuracy: 0.4959 - val_loss: 26.6614 - learning_rate: 1.0000e-04
Epoch 1966/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 6.6584e-06 - val_accuracy: 0.4976 - val_loss: 26.6390 - learning_rate: 1.0000e-04
Epoch 1967/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 7.4794e-06 - val_accuracy: 0.4976 - val_loss: 26.6062 - learning_rate: 1.0000e-04
Epoch 1968/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 1.0385e-05 - val_accuracy: 0.4976 - val_loss: 26.5611 - learning_rate: 1.0000e-04
Epoch 1969/2000
37/37 ━━━━

In [6]:
#ResN-5
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('relu')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('relu')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('relu')(conv_z)
     
   # shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
   # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
    shortcut_y = keras.layers.BatchNormalization()(x)    
    #shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_z])
    y = keras.layers.Activation('relu')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist5 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log5 = pd.DataFrame(hist5.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model5 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 6s 37ms/step - accuracy: 0.5438 - loss: 0.6804 - val_accuracy: 0.3801 - val_loss: 1.8294 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.5119 - loss: 0.6951 - val_accuracy: 0.6199 - val_loss: 2.1352 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.5576 - loss: 0.6785 - val_accuracy: 0.6199 - val_loss: 1.5864 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.5772 - loss: 0.6893 - val_accuracy: 0.6199 - val_loss: 1.9210 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.5831 - loss: 0.6786 - val_accuracy: 0.6199 - val_loss: 0.7289 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5677 - loss: 0.6876 - val_accuracy: 0.6199 - val_loss: 1.4278 - learning_rate

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.6866 - loss: 0.5907 - val_accuracy: 0.6297 - val_loss: 1.9238 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6980 - loss: 0.5928 - val_accuracy: 0.5432 - val_loss: 0.8664 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7333 - loss: 0.5635 - val_accuracy: 0.6509 - val_loss: 1.0781 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6815 - loss: 0.5958 - val_accuracy: 0.6688 - val_loss: 0.6824 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7127 - loss: 0.5650 - val_accuracy: 0.6558 - val_loss: 0.9166 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.6631 - loss: 0.5958 - val_accuracy: 0.5710 - val_loss: 0.8364 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6964 - loss: 0.5905 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7328 - loss: 0.5644 - val_accuracy: 0.6754 - val_loss: 0.8572 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7227 - loss: 0.5677 - val_accuracy: 0.6215 - val_loss: 1.0202 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7241 - loss: 0.5488 - val_accuracy: 0.6770 - val_loss: 0.9462 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6935 - loss: 0.5584 - val_accuracy: 0.5334 - val_loss: 1.4006 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6980 - loss: 0.5802 - val_accuracy: 0.5791 - val_loss: 1.2095 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7322 - loss: 0.5689 - val_accuracy: 0.5041 - val_loss: 1.9395 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7167 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7358 - loss: 0.5263 - val_accuracy: 0.4502 - val_loss: 3.7346 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7465 - loss: 0.5064 - val_accuracy: 0.4878 - val_loss: 2.6181 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7380 - loss: 0.5323 - val_accuracy: 0.4959 - val_loss: 2.6552 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7298 - loss: 0.5442 - val_accuracy: 0.4943 - val_loss: 2.6168 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7212 - loss: 0.5491 - val_accuracy: 0.4649 - val_loss: 3.6847 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7468 - loss: 0.5383 - val_accuracy: 0.5416 - val_loss: 1.9404 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7295 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7417 - loss: 0.5421 - val_accuracy: 0.4715 - val_loss: 4.4602 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7174 - loss: 0.5468 - val_accuracy: 0.4682 - val_loss: 4.5021 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7740 - loss: 0.5062 - val_accuracy: 0.4437 - val_loss: 5.7175 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7539 - loss: 0.5237 - val_accuracy: 0.4535 - val_loss: 5.3120 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7307 - loss: 0.5326 - val_accuracy: 0.6509 - val_loss: 1.2927 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7326 - loss: 0.5567 - val_accuracy: 0.4421 - val_loss: 5.8218 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7776 - loss: 0.5

...

Epoch 1792/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0088 - val_accuracy: 0.4127 - val_loss: 178.5601 - learning_rate: 1.2500e-04
Epoch 1793/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0102 - val_accuracy: 0.4127 - val_loss: 180.6240 - learning_rate: 1.2500e-04
Epoch 1794/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0073 - val_accuracy: 0.4127 - val_loss: 178.4352 - learning_rate: 1.2500e-04
Epoch 1795/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0074 - val_accuracy: 0.4095 - val_loss: 184.2143 - learning_rate: 1.2500e-04
Epoch 1796/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0081 - val_accuracy: 0.4127 - val_loss: 180.9063 - learning_rate: 1.2500e-04
Epoch 1797/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0061 - val_accuracy: 0.4127 - val_loss: 179.4996 - learning_rate: 1.2500e-04
Epoch 1798/2000
37/37 ━━━━━━

Epoch 1834/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0066 - val_accuracy: 0.4095 - val_loss: 184.7545 - learning_rate: 1.2500e-04
Epoch 1835/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0087 - val_accuracy: 0.4127 - val_loss: 183.1727 - learning_rate: 1.2500e-04
Epoch 1836/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0078 - val_accuracy: 0.4127 - val_loss: 181.9615 - learning_rate: 1.2500e-04
Epoch 1837/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0070 - val_accuracy: 0.4095 - val_loss: 186.1346 - learning_rate: 1.2500e-04
Epoch 1838/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0079 - val_accuracy: 0.4144 - val_loss: 181.7168 - learning_rate: 1.2500e-04
Epoch 1839/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0073 - val_accuracy: 0.4095 - val_loss: 184.8774 - learning_rate: 1.2500e-04
Epoch 1840/2000
37/37 ━━━━━━

Epoch 1876/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0073 - val_accuracy: 0.4144 - val_loss: 186.1078 - learning_rate: 1.2500e-04
Epoch 1877/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0062 - val_accuracy: 0.4111 - val_loss: 187.9154 - learning_rate: 1.2500e-04
Epoch 1878/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.9986 - loss: 0.0069 - val_accuracy: 0.4095 - val_loss: 188.9677 - learning_rate: 1.2500e-04
Epoch 1879/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 0.0063 - val_accuracy: 0.4127 - val_loss: 185.4935 - learning_rate: 1.2500e-04
Epoch 1880/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0068 - val_accuracy: 0.4111 - val_loss: 186.8187 - learning_rate: 1.2500e-04
Epoch 1881/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0086 - val_accuracy: 0.4144 - val_loss: 183.0821 - learning_rate: 1.2500e-04
Epoch 1882/2000
37/37 ━━━━━━

Epoch 1918/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0059 - val_accuracy: 0.4095 - val_loss: 193.0304 - learning_rate: 1.2500e-04
Epoch 1919/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0068 - val_accuracy: 0.4144 - val_loss: 189.4674 - learning_rate: 1.2500e-04
Epoch 1920/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0066 - val_accuracy: 0.4095 - val_loss: 192.8760 - learning_rate: 1.2500e-04
Epoch 1921/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0068 - val_accuracy: 0.4127 - val_loss: 189.9681 - learning_rate: 1.2500e-04
Epoch 1922/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0057 - val_accuracy: 0.4111 - val_loss: 189.6928 - learning_rate: 1.2500e-04
Epoch 1923/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0068 - val_accuracy: 0.4095 - val_loss: 192.7586 - learning_rate: 1.2500e-04
Epoch 1924/2000
37/37 ━━━━━━

Epoch 1960/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0056 - val_accuracy: 0.4111 - val_loss: 188.5287 - learning_rate: 1.2500e-04
Epoch 1961/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0071 - val_accuracy: 0.4111 - val_loss: 195.5627 - learning_rate: 1.2500e-04
Epoch 1962/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 0.0076 - val_accuracy: 0.4111 - val_loss: 192.3925 - learning_rate: 1.2500e-04
Epoch 1963/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 0.0069 - val_accuracy: 0.4127 - val_loss: 193.3463 - learning_rate: 1.2500e-04
Epoch 1964/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0056 - val_accuracy: 0.4127 - val_loss: 194.6145 - learning_rate: 1.2500e-04
Epoch 1965/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0058 - val_accuracy: 0.4127 - val_loss: 193.0403 - learning_rate: 1.2500e-04
Epoch 1966/2000
37/37 ━━━━━━

In [7]:
#ResN-6
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('relu')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('relu')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('relu')(conv_z)
    
    print ('build conv_w')
    conv_w = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_z)
    conv_w = keras.layers.Activation('relu')(conv_w)
     
   # shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
   # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
    shortcut_y = keras.layers.BatchNormalization()(x)    
    #shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_w])
    y = keras.layers.Activation('relu')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist6 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log6 = pd.DataFrame(hist6.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model6 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
build conv_w
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 8s 55ms/step - accuracy: 0.5246 - loss: 0.7031 - val_accuracy: 0.6199 - val_loss: 1.4785 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 29ms/step - accuracy: 0.5741 - loss: 0.6873 - val_accuracy: 0.6199 - val_loss: 0.6899 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.5397 - loss: 0.6902 - val_accuracy: 0.6199 - val_loss: 2.2074 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.5896 - loss: 0.6790 - val_accuracy: 0.6199 - val_loss: 0.8368 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6083 - loss: 0.6779 - val_accuracy: 0.3801 - val_loss: 1.3007 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.5611 - loss: 0.6865 - val_accuracy: 0.6199 - val_loss: 1.5005 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6945 - loss: 0.5781 - val_accuracy: 0.6639 - val_loss: 0.7816 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6434 - loss: 0.6067 - val_accuracy: 0.6101 - val_loss: 0.9399 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7039 - loss: 0.5784 - val_accuracy: 0.7047 - val_loss: 0.6908 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7162 - loss: 0.5677 - val_accuracy: 0.6786 - val_loss: 0.7885 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6982 - loss: 0.5734 - val_accuracy: 0.6868 - val_loss: 0.7503 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7111 - loss: 0.5558 - val_accuracy: 0.4992 - val_loss: 1.3688 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6959 - loss: 0.5797 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6764 - loss: 0.5698 - val_accuracy: 0.6868 - val_loss: 1.0546 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7326 - loss: 0.5478 - val_accuracy: 0.6101 - val_loss: 1.4378 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6758 - loss: 0.5734 - val_accuracy: 0.6884 - val_loss: 1.1993 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7060 - loss: 0.5622 - val_accuracy: 0.6868 - val_loss: 1.0939 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7286 - loss: 0.5528 - val_accuracy: 0.5122 - val_loss: 3.4256 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6910 - loss: 0.5930 - val_accuracy: 0.7064 - val_loss: 0.7827 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7152 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7324 - loss: 0.5251 - val_accuracy: 0.4666 - val_loss: 7.0168 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 25ms/step - accuracy: 0.7009 - loss: 0.5801 - val_accuracy: 0.4861 - val_loss: 5.3520 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7235 - loss: 0.5559 - val_accuracy: 0.4666 - val_loss: 6.8179 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7040 - loss: 0.5704 - val_accuracy: 0.4682 - val_loss: 5.3861 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7163 - loss: 0.5208 - val_accuracy: 0.4796 - val_loss: 5.4643 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7128 - loss: 0.5499 - val_accuracy: 0.5840 - val_loss: 2.4779 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7213 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7430 - loss: 0.5182 - val_accuracy: 0.4421 - val_loss: 11.3127 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7768 - loss: 0.4817 - val_accuracy: 0.6411 - val_loss: 2.0550 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7529 - loss: 0.5238 - val_accuracy: 0.6803 - val_loss: 1.4162 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7365 - loss: 0.5289 - val_accuracy: 0.4861 - val_loss: 6.7986 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7397 - loss: 0.5079 - val_accuracy: 0.4780 - val_loss: 5.0118 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7100 - loss: 0.5222 - val_accuracy: 0.5106 - val_loss: 5.7793 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7581 - loss: 0.

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 7.5561e-05 - val_accuracy: 0.6330 - val_loss: 35.3143 - learning_rate: 1.0000e-04
Epoch 1812/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 7.0317e-05 - val_accuracy: 0.6330 - val_loss: 35.0561 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 5.2628e-05 - val_accuracy: 0.6346 - val_loss: 34.8424 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 7.9663e-05 - val_accuracy: 0.6362 - val_loss: 34.6855 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 9.8601e-05 - val_accuracy: 0.6346 - val_loss: 34.5177 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 7.2636e-05 - val_accuracy: 0.6330 - val_loss: 34.3373 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 1.0000 - loss: 4.3281e-05 - val_accuracy: 0.6688 - val_loss: 30.6784 - learning_rate: 1.0000e-04
Epoch 1853/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 1.0000 - loss: 3.8794e-05 - val_accuracy: 0.6672 - val_loss: 30.5772 - learning_rate: 1.0000e-04
Epoch 1854/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 1.0000 - loss: 3.1204e-05 - val_accuracy: 0.6688 - val_loss: 30.5414 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 4.1164e-05 - val_accuracy: 0.6737 - val_loss: 30.4252 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 5.9903e-05 - val_accuracy: 0.6721 - val_loss: 30.3519 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 1.0000 - loss: 3.6696e-05 - val_accuracy: 0.6737 - val_loss: 30.2517 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 3.8600e-05 - val_accuracy: 0.6900 - val_loss: 28.6457 - learning_rate: 1.0000e-04
Epoch 1894/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 3.8295e-05 - val_accuracy: 0.6917 - val_loss: 28.6250 - learning_rate: 1.0000e-04
Epoch 1895/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 4.1409e-05 - val_accuracy: 0.6917 - val_loss: 28.6188 - learning_rate: 1.0000e-04
Epoch 1896/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 1.0000 - loss: 3.3208e-05 - val_accuracy: 0.6917 - val_loss: 28.5973 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 1.0000 - loss: 4.0582e-05 - val_accuracy: 0.6917 - val_loss: 28.5784 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 3.9551e-05 - val_accuracy: 0.6933 - val_loss: 28.5325 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 3.3088e-05 - val_accuracy: 0.6917 - val_loss: 28.3452 - learning_rate: 1.0000e-04
Epoch 1935/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 2.2020e-05 - val_accuracy: 0.6900 - val_loss: 28.4021 - learning_rate: 1.0000e-04
Epoch 1936/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 3.5437e-05 - val_accuracy: 0.6933 - val_loss: 28.3358 - learning_rate: 1.0000e-04
Epoch 1937/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 2.1220e-05 - val_accuracy: 0.6884 - val_loss: 28.3931 - learning_rate: 1.0000e-04
Epoch 1938/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 2.6504e-05 - val_accuracy: 0.6949 - val_loss: 28.3324 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 3.5388e-05 - val_accuracy: 0.6900 - val_loss: 28.4417 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 1.9352e-05 - val_accuracy: 0.6900 - val_loss: 28.3945 - learning_rate: 1.0000e-04
Epoch 1976/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 2.6556e-05 - val_accuracy: 0.6900 - val_loss: 28.3392 - learning_rate: 1.0000e-04
Epoch 1977/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 1.8113e-05 - val_accuracy: 0.6884 - val_loss: 28.3368 - learning_rate: 1.0000e-04
Epoch 1978/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 2.5304e-05 - val_accuracy: 0.6900 - val_loss: 28.3808 - learning_rate: 1.0000e-04
Epoch 1979/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 2.0572e-05 - val_accuracy: 0.6917 - val_loss: 28.3220 - learning_rate: 1.0000e-04
Epoch 1980/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 2.3758e-05 - val_accuracy: 0.6884 - val_loss: 28.3848 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━

In [8]:
#ResN-7
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('relu')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('relu')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('relu')(conv_z)
     
   # shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
   # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
   # shortcut_y = keras.layers.BatchNormalization()(x)    
    shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_z])
    y = keras.layers.Activation('relu')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist7 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log7 = pd.DataFrame(hist7.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model7 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 6s 43ms/step - accuracy: 0.5037 - loss: 0.7396 - val_accuracy: 0.6199 - val_loss: 2.0287 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5677 - loss: 0.6959 - val_accuracy: 0.6199 - val_loss: 1.1355 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.5818 - loss: 0.6815 - val_accuracy: 0.5563 - val_loss: 0.6892 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.5706 - loss: 0.6884 - val_accuracy: 0.6199 - val_loss: 1.7312 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.5636 - loss: 0.6843 - val_accuracy: 0.6199 - val_loss: 0.6677 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.5858 - loss: 0.6798 - val_accuracy: 0.6199 - val_loss: 0.6678 - learning_rate

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6819 - loss: 0.5919 - val_accuracy: 0.6737 - val_loss: 0.6680 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7119 - loss: 0.5675 - val_accuracy: 0.4551 - val_loss: 1.5816 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6746 - loss: 0.6084 - val_accuracy: 0.4405 - val_loss: 1.7243 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 27ms/step - accuracy: 0.7057 - loss: 0.5843 - val_accuracy: 0.6803 - val_loss: 0.7029 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6899 - loss: 0.5869 - val_accuracy: 0.6362 - val_loss: 1.6021 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6810 - loss: 0.5889 - val_accuracy: 0.4551 - val_loss: 1.6228 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6893 - loss: 0.5884 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7097 - loss: 0.5501 - val_accuracy: 0.6656 - val_loss: 0.9028 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7221 - loss: 0.5616 - val_accuracy: 0.4160 - val_loss: 2.8628 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7144 - loss: 0.5620 - val_accuracy: 0.6542 - val_loss: 1.4495 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7588 - loss: 0.5208 - val_accuracy: 0.6574 - val_loss: 1.4360 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6801 - loss: 0.5773 - val_accuracy: 0.4666 - val_loss: 1.6750 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6817 - loss: 0.5857 - val_accuracy: 0.6101 - val_loss: 0.9198 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7074 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6792 - loss: 0.5671 - val_accuracy: 0.4617 - val_loss: 3.3199 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7211 - loss: 0.5544 - val_accuracy: 0.7064 - val_loss: 0.9391 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7110 - loss: 0.5638 - val_accuracy: 0.5334 - val_loss: 2.0045 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6966 - loss: 0.5715 - val_accuracy: 0.5367 - val_loss: 1.9645 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6911 - loss: 0.5554 - val_accuracy: 0.3980 - val_loss: 7.1303 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6989 - loss: 0.5626 - val_accuracy: 0.7096 - val_loss: 0.9560 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7513 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7491 - loss: 0.5321 - val_accuracy: 0.4666 - val_loss: 4.9959 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7181 - loss: 0.5522 - val_accuracy: 0.4486 - val_loss: 6.5727 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6868 - loss: 0.5545 - val_accuracy: 0.4144 - val_loss: 9.5379 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7108 - loss: 0.5547 - val_accuracy: 0.4535 - val_loss: 6.0428 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6948 - loss: 0.5631 - val_accuracy: 0.4274 - val_loss: 8.5387 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7286 - loss: 0.5446 - val_accuracy: 0.4763 - val_loss: 5.2207 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7373 - loss: 0.5

...

Epoch 1795/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.9892 - loss: 0.0333 - val_accuracy: 0.4258 - val_loss: 131.6486 - learning_rate: 1.2500e-04
Epoch 1796/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.9963 - loss: 0.0279 - val_accuracy: 0.4209 - val_loss: 135.9248 - learning_rate: 1.2500e-04
Epoch 1797/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.9873 - loss: 0.0369 - val_accuracy: 0.4209 - val_loss: 138.4883 - learning_rate: 1.2500e-04
Epoch 1798/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.9846 - loss: 0.0389 - val_accuracy: 0.4241 - val_loss: 130.0265 - learning_rate: 1.2500e-04
Epoch 1799/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.9941 - loss: 0.0334 - val_accuracy: 0.4209 - val_loss: 134.9236 - learning_rate: 1.2500e-04
Epoch 1800/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.9885 - loss: 0.0327 - val_accuracy: 0.4209 - val_loss: 135.1962 - learning_rate: 1.2500e-04
Epoch 1801/2000
37/37 ━━━━━━

Epoch 1837/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.9946 - loss: 0.0334 - val_accuracy: 0.4258 - val_loss: 134.8051 - learning_rate: 1.2500e-04
Epoch 1838/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.9933 - loss: 0.0327 - val_accuracy: 0.4241 - val_loss: 132.9054 - learning_rate: 1.2500e-04
Epoch 1839/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.9985 - loss: 0.0275 - val_accuracy: 0.4258 - val_loss: 133.7437 - learning_rate: 1.2500e-04
Epoch 1840/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.9939 - loss: 0.0292 - val_accuracy: 0.4258 - val_loss: 134.2285 - learning_rate: 1.2500e-04
Epoch 1841/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9956 - loss: 0.0253 - val_accuracy: 0.4241 - val_loss: 131.9750 - learning_rate: 1.2500e-04
Epoch 1842/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9944 - loss: 0.0309 - val_accuracy: 0.4209 - val_loss: 138.8830 - learning_rate: 1.2500e-04
Epoch 1843/2000
37/37 ━━━━━━

Epoch 1879/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.9921 - loss: 0.0286 - val_accuracy: 0.4258 - val_loss: 132.9687 - learning_rate: 1.2500e-04
Epoch 1880/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.9936 - loss: 0.0274 - val_accuracy: 0.4258 - val_loss: 133.8420 - learning_rate: 1.2500e-04
Epoch 1881/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9943 - loss: 0.0281 - val_accuracy: 0.4258 - val_loss: 132.6159 - learning_rate: 1.2500e-04
Epoch 1882/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9935 - loss: 0.0259 - val_accuracy: 0.4258 - val_loss: 133.7778 - learning_rate: 1.2500e-04
Epoch 1883/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9966 - loss: 0.0263 - val_accuracy: 0.4274 - val_loss: 131.1308 - learning_rate: 1.2500e-04
Epoch 1884/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.9912 - loss: 0.0329 - val_accuracy: 0.4274 - val_loss: 133.5586 - learning_rate: 1.2500e-04
Epoch 1885/2000
37/37 ━━━━━━

Epoch 1921/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9899 - loss: 0.0325 - val_accuracy: 0.4258 - val_loss: 140.2797 - learning_rate: 1.2500e-04
Epoch 1922/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.9938 - loss: 0.0236 - val_accuracy: 0.4258 - val_loss: 140.4959 - learning_rate: 1.2500e-04
Epoch 1923/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9960 - loss: 0.0231 - val_accuracy: 0.4258 - val_loss: 135.2414 - learning_rate: 1.2500e-04
Epoch 1924/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9932 - loss: 0.0262 - val_accuracy: 0.4258 - val_loss: 140.0572 - learning_rate: 1.2500e-04
Epoch 1925/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9882 - loss: 0.0336 - val_accuracy: 0.4290 - val_loss: 134.1679 - learning_rate: 1.2500e-04
Epoch 1926/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9867 - loss: 0.0300 - val_accuracy: 0.4258 - val_loss: 137.5849 - learning_rate: 1.2500e-04
Epoch 1927/2000
37/37 ━━━━━━

Epoch 1963/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.9976 - loss: 0.0225 - val_accuracy: 0.4274 - val_loss: 138.7163 - learning_rate: 1.2500e-04
Epoch 1964/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9908 - loss: 0.0294 - val_accuracy: 0.4274 - val_loss: 142.5805 - learning_rate: 1.2500e-04
Epoch 1965/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.9922 - loss: 0.0317 - val_accuracy: 0.4258 - val_loss: 140.5318 - learning_rate: 1.2500e-04
Epoch 1966/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9911 - loss: 0.0295 - val_accuracy: 0.4258 - val_loss: 142.1202 - learning_rate: 1.2500e-04
Epoch 1967/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9908 - loss: 0.0245 - val_accuracy: 0.4258 - val_loss: 139.6295 - learning_rate: 1.2500e-04
Epoch 1968/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.9957 - loss: 0.0255 - val_accuracy: 0.4274 - val_loss: 140.5326 - learning_rate: 1.2500e-04
Epoch 1969/2000
37/37 ━━━━━━

In [9]:
#ResN-8
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('relu')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('relu')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('relu')(conv_z)
    
    print ('build conv_w')
    conv_w = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_z)
    conv_w = keras.layers.Activation('relu')(conv_w)
     
   # shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
   # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
   # shortcut_y = keras.layers.BatchNormalization()(x)    
    shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_w])
    y = keras.layers.Activation('relu')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist8 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log8 = pd.DataFrame(hist8.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model8 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
build conv_w
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 8s 54ms/step - accuracy: 0.5054 - loss: 0.6915 - val_accuracy: 0.6199 - val_loss: 2.0184 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5599 - loss: 0.6809 - val_accuracy: 0.6199 - val_loss: 2.5743 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 33ms/step - accuracy: 0.5483 - loss: 0.6952 - val_accuracy: 0.6199 - val_loss: 0.9421 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.5558 - loss: 0.6951 - val_accuracy: 0.6199 - val_loss: 0.6685 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.5808 - loss: 0.6866 - val_accuracy: 0.6199 - val_loss: 1.2320 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.5585 - loss: 0.6902 - val_accuracy: 0.3997 - val_loss: 0.7721 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6783 - loss: 0.5941 - val_accuracy: 0.5008 - val_loss: 1.2749 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7001 - loss: 0.6078 - val_accuracy: 0.4078 - val_loss: 3.0995 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7031 - loss: 0.5752 - val_accuracy: 0.4486 - val_loss: 2.0224 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7085 - loss: 0.5723 - val_accuracy: 0.6835 - val_loss: 0.6581 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6733 - loss: 0.5899 - val_accuracy: 0.3964 - val_loss: 4.1424 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7109 - loss: 0.5565 - val_accuracy: 0.7031 - val_loss: 0.6559 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7069 - loss: 0.5884 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6693 - loss: 0.5999 - val_accuracy: 0.6868 - val_loss: 0.8641 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7111 - loss: 0.5788 - val_accuracy: 0.5106 - val_loss: 2.0349 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6983 - loss: 0.5523 - val_accuracy: 0.6819 - val_loss: 0.9511 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7223 - loss: 0.5541 - val_accuracy: 0.6688 - val_loss: 1.1951 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6880 - loss: 0.5687 - val_accuracy: 0.4812 - val_loss: 2.7320 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6781 - loss: 0.6073 - val_accuracy: 0.5546 - val_loss: 1.7232 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7239 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7435 - loss: 0.5347 - val_accuracy: 0.3948 - val_loss: 11.0386 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6696 - loss: 0.5917 - val_accuracy: 0.6150 - val_loss: 1.5979 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7137 - loss: 0.5587 - val_accuracy: 0.5237 - val_loss: 2.7909 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7296 - loss: 0.5546 - val_accuracy: 0.4698 - val_loss: 4.3998 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6675 - loss: 0.5928 - val_accuracy: 0.6444 - val_loss: 1.4113 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7470 - loss: 0.5345 - val_accuracy: 0.4062 - val_loss: 9.2930 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7335 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7394 - loss: 0.5090 - val_accuracy: 0.4437 - val_loss: 5.9581 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7407 - loss: 0.5497 - val_accuracy: 0.4192 - val_loss: 8.7185 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 25ms/step - accuracy: 0.7155 - loss: 0.5505 - val_accuracy: 0.4551 - val_loss: 5.8164 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7556 - loss: 0.5163 - val_accuracy: 0.4144 - val_loss: 10.4939 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7414 - loss: 0.5109 - val_accuracy: 0.4127 - val_loss: 10.2091 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7549 - loss: 0.5084 - val_accuracy: 0.4029 - val_loss: 11.9619 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7219 - loss: 

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0037 - val_accuracy: 0.5122 - val_loss: 58.4210 - learning_rate: 1.2500e-04
Epoch 1830/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0058 - val_accuracy: 0.5139 - val_loss: 58.0269 - learning_rate: 1.2500e-04
Epoch 1831/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 0.0057 - val_accuracy: 0.5122 - val_loss: 58.5626 - learning_rate: 1.2500e-04
Epoch 1832/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0064 - val_accuracy: 0.5155 - val_loss: 57.4337 - learning_rate: 1.2500e-04
Epoch 1833/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 1.0000 - loss: 0.0050 - val_accuracy: 0.5155 - val_loss: 57.6420 - learning_rate: 1.2500e-04
Epoch 1834/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0037 - val_accuracy: 0.5204 - val_loss: 56.6594 - learning_rate: 1.2500e-04
Epoch 1835/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0049 - val_accuracy: 0.5171 - val_loss: 56.8172 - learning_rate: 1.2500e-04
Epoch 1872/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0041 - val_accuracy: 0.5188 - val_loss: 55.4374 - learning_rate: 1.2500e-04
Epoch 1873/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 0.0059 - val_accuracy: 0.5204 - val_loss: 56.1327 - learning_rate: 1.2500e-04
Epoch 1874/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 0.0039 - val_accuracy: 0.5171 - val_loss: 55.7645 - learning_rate: 1.2500e-04
Epoch 1875/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9996 - loss: 0.0044 - val_accuracy: 0.5057 - val_loss: 64.2940 - learning_rate: 1.2500e-04
Epoch 1876/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.9971 - loss: 0.0221 - val_accuracy: 0.4976 - val_loss: 67.7867 - learning_rate: 1.2500e-04
Epoch 1877/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0023 - val_accuracy: 0.5188 - val_loss: 55.8842 - learning_rate: 1.2500e-04
Epoch 1914/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0038 - val_accuracy: 0.5155 - val_loss: 56.6811 - learning_rate: 1.2500e-04
Epoch 1915/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0038 - val_accuracy: 0.5237 - val_loss: 53.5918 - learning_rate: 1.2500e-04
Epoch 1916/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0038 - val_accuracy: 0.5139 - val_loss: 58.1010 - learning_rate: 1.2500e-04
Epoch 1917/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0041 - val_accuracy: 0.5204 - val_loss: 55.2201 - learning_rate: 1.2500e-04
Epoch 1918/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 0.0035 - val_accuracy: 0.5139 - val_loss: 56.8027 - learning_rate: 1.2500e-04
Epoch 1919/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 0.0026 - val_accuracy: 0.5237 - val_loss: 52.2523 - learning_rate: 1.2500e-04
Epoch 1956/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0036 - val_accuracy: 0.5220 - val_loss: 52.3012 - learning_rate: 1.2500e-04
Epoch 1957/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 0.0045 - val_accuracy: 0.5204 - val_loss: 54.7990 - learning_rate: 1.2500e-04
Epoch 1958/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 1.0000 - loss: 0.0049 - val_accuracy: 0.5237 - val_loss: 52.1062 - learning_rate: 1.2500e-04
Epoch 1959/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 28ms/step - accuracy: 1.0000 - loss: 0.0030 - val_accuracy: 0.5204 - val_loss: 53.7062 - learning_rate: 1.2500e-04
Epoch 1960/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 1.0000 - loss: 0.0038 - val_accuracy: 0.5188 - val_loss: 54.4482 - learning_rate: 1.2500e-04
Epoch 1961/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.9954 - loss: 0.0227 - val_accuracy: 0.5171 - val_loss: 56.0815 - learning_rate: 1.2500e-04
Epoch 1998/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 1.0000 - loss: 0.0044 - val_accuracy: 0.5220 - val_loss: 48.7163 - learning_rate: 1.2500e-04
Epoch 1999/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.9979 - loss: 0.0071 - val_accuracy: 0.5269 - val_loss: 49.3459 - learning_rate: 1.2500e-04
Epoch 2000/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 0.0031 - val_accuracy: 0.5237 - val_loss: 49.9409 - learning_rate: 1.2500e-04


In [10]:
#ResN-9
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('linear')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('linear')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('linear')(conv_z)
    
    
    shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
   # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
   # shortcut_y = keras.layers.BatchNormalization()(x)    
    #shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_z])
    y = keras.layers.Activation('linear')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist9 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log9 = pd.DataFrame(hist9.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model9 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 6s 33ms/step - accuracy: 0.5713 - loss: 0.6870 - val_accuracy: 0.6199 - val_loss: 0.7147 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.5457 - loss: 0.6835 - val_accuracy: 0.6199 - val_loss: 1.3056 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6057 - loss: 0.6661 - val_accuracy: 0.6199 - val_loss: 2.5020 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.5785 - loss: 0.6882 - val_accuracy: 0.3801 - val_loss: 1.3109 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.5929 - loss: 0.6637 - val_accuracy: 0.6248 - val_loss: 1.8585 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6356 - loss: 0.6597 - val_accuracy: 0.6199 - val_loss: 1.6359 - learning_rate

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6998 - loss: 0.5825 - val_accuracy: 0.6623 - val_loss: 0.9880 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7352 - loss: 0.5825 - val_accuracy: 0.4845 - val_loss: 1.4573 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7008 - loss: 0.5618 - val_accuracy: 0.5954 - val_loss: 0.9357 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6709 - loss: 0.5976 - val_accuracy: 0.6264 - val_loss: 0.9491 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7206 - loss: 0.5783 - val_accuracy: 0.6656 - val_loss: 0.8099 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7150 - loss: 0.5884 - val_accuracy: 0.7096 - val_loss: 0.7196 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7110 - loss: 0.5719 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6905 - loss: 0.5837 - val_accuracy: 0.6639 - val_loss: 1.0580 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 23ms/step - accuracy: 0.7161 - loss: 0.5838 - val_accuracy: 0.6852 - val_loss: 0.7612 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6994 - loss: 0.5804 - val_accuracy: 0.5954 - val_loss: 0.9055 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7298 - loss: 0.5562 - val_accuracy: 0.6509 - val_loss: 1.4518 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7031 - loss: 0.5778 - val_accuracy: 0.6525 - val_loss: 1.6974 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6971 - loss: 0.5857 - val_accuracy: 0.6852 - val_loss: 0.8259 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7210 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7218 - loss: 0.5617 - val_accuracy: 0.6591 - val_loss: 1.3961 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7381 - loss: 0.5427 - val_accuracy: 0.6917 - val_loss: 0.7311 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.6966 - loss: 0.5645 - val_accuracy: 0.6835 - val_loss: 0.7994 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6950 - loss: 0.5757 - val_accuracy: 0.5449 - val_loss: 1.1940 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7253 - loss: 0.5583 - val_accuracy: 0.6770 - val_loss: 0.7761 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7297 - loss: 0.5710 - val_accuracy: 0.6754 - val_loss: 0.9807 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6957 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7251 - loss: 0.5505 - val_accuracy: 0.6949 - val_loss: 0.7371 - learning_rate: 5.0000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7328 - loss: 0.5712 - val_accuracy: 0.6900 - val_loss: 0.8030 - learning_rate: 5.0000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6991 - loss: 0.5948 - val_accuracy: 0.6786 - val_loss: 0.9183 - learning_rate: 5.0000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7048 - loss: 0.5663 - val_accuracy: 0.6639 - val_loss: 1.2361 - learning_rate: 5.0000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7176 - loss: 0.5771 - val_accuracy: 0.6803 - val_loss: 1.0071 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7259 - loss: 0.5468 - val_accuracy: 0.7145 - val_loss: 0.7156 - learning_rate: 5.0000e-04
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7221 - loss: 0.5782 - val_accuracy: 0.6933 - val_loss: 0.7952 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7306 - loss: 0.5462 - val_accuracy: 0.7015 - val_loss: 0.7743 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6986 - loss: 0.5812 - val_accuracy: 0.6835 - val_loss: 0.8504 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7163 - loss: 0.5500 - val_accuracy: 0.7031 - val_loss: 0.7720 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6844 - loss: 0.5573 - val_accuracy: 0.6966 - val_loss: 0.7822 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7078 - loss: 0.5578 - val_accuracy: 0.6900 - val_loss: 0.8229 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6564 - loss: 0.6110 - val_accuracy: 0.6835 - val_loss: 0.8585 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6860 - loss: 0.5732 - val_accuracy: 0.6966 - val_loss: 0.8032 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.7118 - loss: 0.5711 - val_accuracy: 0.6966 - val_loss: 0.7783 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6954 - loss: 0.5589 - val_accuracy: 0.6835 - val_loss: 0.8828 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7467 - loss: 0.5426 - val_accuracy: 0.7031 - val_loss: 0.7631 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6974 - loss: 0.5670 - val_accuracy: 0.6884 - val_loss: 0.8279 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6955 - loss: 0.5609 - val_accuracy: 0.6966 - val_loss: 0.7784 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7014 - loss: 0.5812 - val_accuracy: 0.7080 - val_loss: 0.7485 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7352 - loss: 0.5447 - val_accuracy: 0.6966 - val_loss: 0.7944 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.6993 - loss: 0.5616 - val_accuracy: 0.7015 - val_loss: 0.7754 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7082 - loss: 0.5562 - val_accuracy: 0.6835 - val_loss: 0.8296 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7155 - loss: 0.5634 - val_accuracy: 0.7031 - val_loss: 0.7605 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7331 - loss: 0.5212 - val_accuracy: 0.6852 - val_loss: 0.8456 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7127 - loss: 0.5604 - val_accuracy: 0.6917 - val_loss: 0.7870 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7002 - loss: 0.5471 - val_accuracy: 0.6982 - val_loss: 0.8128 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7095 - loss: 0.5637 - val_accuracy: 0.6949 - val_loss: 0.7946 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7028 - loss: 0.5659 - val_accuracy: 0.7015 - val_loss: 0.7744 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7039 - loss: 0.5529 - val_accuracy: 0.6982 - val_loss: 0.7977 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7037 - loss: 0.5655 - val_accuracy: 0.6949 - val_loss: 0.7896 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7033 - loss: 0.5731 - val_accuracy: 0.6852 - val_loss: 0.8308 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7150 - loss: 0.5834 - val_accuracy: 0.7047 - val_loss: 0.7555 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7205 - loss: 0.5417 - val_accuracy: 0.6835 - val_loss: 0.8506 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7241 - loss: 0.5371 - val_accuracy: 0.7096 - val_loss: 0.7400 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7128 - loss: 0.5616 - val_accuracy: 0.6966 - val_loss: 0.7912 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step 

In [11]:
#ResN-10
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('linear')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('linear')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('linear')(conv_z)
    
    print ('build conv_w')
    conv_w = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_z)
    conv_w = keras.layers.Activation('linear')(conv_w)
     
    shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
   # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
   # shortcut_y = keras.layers.BatchNormalization()(x)    
    #shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_w])
    y = keras.layers.Activation('linear')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist10 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log10 = pd.DataFrame(hist10.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model10 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
build conv_w
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 4s 28ms/step - accuracy: 0.5633 - loss: 0.6883 - val_accuracy: 0.6199 - val_loss: 1.1151 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.5431 - loss: 0.6900 - val_accuracy: 0.6199 - val_loss: 0.9316 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.5501 - loss: 0.6847 - val_accuracy: 0.6199 - val_loss: 1.0615 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.5554 - loss: 0.6849 - val_accuracy: 0.4176 - val_loss: 1.4681 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6310 - loss: 0.6450 - val_accuracy: 0.6248 - val_loss: 3.4511 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6204 - loss: 0.6895 - val_accuracy: 0.6199 - val_loss: 5.6948 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7060 - loss: 0.5994 - val_accuracy: 0.6803 - val_loss: 0.9503 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7182 - loss: 0.5714 - val_accuracy: 0.6346 - val_loss: 2.0764 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6990 - loss: 0.5786 - val_accuracy: 0.6982 - val_loss: 0.6777 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6917 - loss: 0.5839 - val_accuracy: 0.6264 - val_loss: 3.5551 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7159 - loss: 0.5821 - val_accuracy: 0.6868 - val_loss: 0.7178 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6977 - loss: 0.5936 - val_accuracy: 0.6900 - val_loss: 0.8508 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7257 - loss: 0.5878 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7131 - loss: 0.5686 - val_accuracy: 0.6427 - val_loss: 2.3444 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6854 - loss: 0.5961 - val_accuracy: 0.6591 - val_loss: 1.2023 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7287 - loss: 0.5543 - val_accuracy: 0.5416 - val_loss: 1.1908 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7123 - loss: 0.5691 - val_accuracy: 0.7113 - val_loss: 0.7477 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7355 - loss: 0.5382 - val_accuracy: 0.6933 - val_loss: 0.6947 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6742 - loss: 0.5972 - val_accuracy: 0.6966 - val_loss: 0.7451 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7367 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7030 - loss: 0.5749 - val_accuracy: 0.6101 - val_loss: 0.8970 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7284 - loss: 0.5603 - val_accuracy: 0.6998 - val_loss: 0.7024 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7130 - loss: 0.5687 - val_accuracy: 0.6607 - val_loss: 0.8315 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6980 - loss: 0.5590 - val_accuracy: 0.6982 - val_loss: 0.7544 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7007 - loss: 0.5703 - val_accuracy: 0.6591 - val_loss: 1.5119 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7522 - loss: 0.5413 - val_accuracy: 0.6525 - val_loss: 0.7500 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7159 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6945 - loss: 0.5563 - val_accuracy: 0.7129 - val_loss: 0.7366 - learning_rate: 5.0000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7160 - loss: 0.5656 - val_accuracy: 0.7031 - val_loss: 0.7591 - learning_rate: 5.0000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7087 - loss: 0.5557 - val_accuracy: 0.6803 - val_loss: 0.9657 - learning_rate: 5.0000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7287 - loss: 0.5437 - val_accuracy: 0.6852 - val_loss: 0.8498 - learning_rate: 5.0000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7239 - loss: 0.5393 - val_accuracy: 0.6444 - val_loss: 1.7188 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7267 - loss: 0.5663 - val_accuracy: 0.7096 - val_loss: 0.7019 - learning_rate: 5.0000e-04
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6795 - loss: 0.6010 - val_accuracy: 0.6852 - val_loss: 0.8377 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7189 - loss: 0.5557 - val_accuracy: 0.6835 - val_loss: 0.8449 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7103 - loss: 0.5660 - val_accuracy: 0.6933 - val_loss: 0.7803 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7213 - loss: 0.5614 - val_accuracy: 0.6900 - val_loss: 0.8200 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7210 - loss: 0.5532 - val_accuracy: 0.7031 - val_loss: 0.7676 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7279 - loss: 0.5496 - val_accuracy: 0.6966 - val_loss: 0.7822 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7011 - loss: 0.5717 - val_accuracy: 0.6966 - val_loss: 0.7965 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6935 - loss: 0.5840 - val_accuracy: 0.6966 - val_loss: 0.7883 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6989 - loss: 0.5750 - val_accuracy: 0.6966 - val_loss: 0.8029 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6944 - loss: 0.5612 - val_accuracy: 0.6966 - val_loss: 0.8038 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7023 - loss: 0.5557 - val_accuracy: 0.6966 - val_loss: 0.8091 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7163 - loss: 0.5544 - val_accuracy: 0.6982 - val_loss: 0.8139 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7173 - loss: 0.5482 - val_accuracy: 0.6900 - val_loss: 0.8168 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7035 - loss: 0.5589 - val_accuracy: 0.6949 - val_loss: 0.8021 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7279 - loss: 0.5416 - val_accuracy: 0.6835 - val_loss: 0.8324 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7111 - loss: 0.5571 - val_accuracy: 0.6949 - val_loss: 0.7782 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6938 - loss: 0.5899 - val_accuracy: 0.6835 - val_loss: 0.8255 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7171 - loss: 0.5529 - val_accuracy: 0.6900 - val_loss: 0.8178 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7187 - loss: 0.5497 - val_accuracy: 0.6949 - val_loss: 0.7867 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7193 - loss: 0.5696 - val_accuracy: 0.6998 - val_loss: 0.7976 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6617 - loss: 0.5800 - val_accuracy: 0.6949 - val_loss: 0.7953 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7107 - loss: 0.5505 - val_accuracy: 0.6949 - val_loss: 0.7925 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6955 - loss: 0.5722 - val_accuracy: 0.7031 - val_loss: 0.7590 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7131 - loss: 0.5562 - val_accuracy: 0.6982 - val_loss: 0.7756 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6993 - loss: 0.5588 - val_accuracy: 0.6900 - val_loss: 0.8229 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7000 - loss: 0.5641 - val_accuracy: 0.7031 - val_loss: 0.7555 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6600 - loss: 0.5799 - val_accuracy: 0.7015 - val_loss: 0.7609 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7052 - loss: 0.5526 - val_accuracy: 0.6900 - val_loss: 0.8177 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7246 - loss: 0.5394 - val_accuracy: 0.6966 - val_loss: 0.7840 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7259 - loss: 0.5375 - val_accuracy: 0.6966 - val_loss: 0.7966 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

In [12]:
#ResN-11
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('linear')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('linear')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('linear')(conv_z)
    
    
    shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
    shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
   # shortcut_y = keras.layers.BatchNormalization()(x)    
    #shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_z])
    y = keras.layers.Activation('linear')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist11 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log11 = pd.DataFrame(hist11.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model11 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 7s 40ms/step - accuracy: 0.5791 - loss: 0.6981 - val_accuracy: 0.6199 - val_loss: 0.6647 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.5766 - loss: 0.6889 - val_accuracy: 0.3801 - val_loss: 1.2283 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.5449 - loss: 0.6913 - val_accuracy: 0.3817 - val_loss: 1.1368 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.5899 - loss: 0.6767 - val_accuracy: 0.4339 - val_loss: 0.9637 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6033 - loss: 0.6698 - val_accuracy: 0.6803 - val_loss: 0.6097 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6741 - loss: 0.6344 - val_accuracy: 0.7162 - val_loss: 0.6214 - learning_rate

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7266 - loss: 0.5755 - val_accuracy: 0.5661 - val_loss: 1.0682 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7047 - loss: 0.5771 - val_accuracy: 0.5579 - val_loss: 1.0943 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6865 - loss: 0.6068 - val_accuracy: 0.6199 - val_loss: 3.9396 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 24ms/step - accuracy: 0.6954 - loss: 0.5982 - val_accuracy: 0.6770 - val_loss: 0.7628 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7364 - loss: 0.5666 - val_accuracy: 0.4013 - val_loss: 2.8909 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7119 - loss: 0.5810 - val_accuracy: 0.6248 - val_loss: 2.9752 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7059 - loss: 0.5670 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7266 - loss: 0.5659 - val_accuracy: 0.6215 - val_loss: 2.8715 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6954 - loss: 0.5809 - val_accuracy: 0.7047 - val_loss: 0.7244 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6738 - loss: 0.6129 - val_accuracy: 0.6835 - val_loss: 0.7394 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7359 - loss: 0.5596 - val_accuracy: 0.4290 - val_loss: 2.4236 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7002 - loss: 0.5837 - val_accuracy: 0.7047 - val_loss: 0.7202 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6976 - loss: 0.5859 - val_accuracy: 0.6460 - val_loss: 0.9472 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7069 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7093 - loss: 0.5789 - val_accuracy: 0.6411 - val_loss: 1.9142 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7458 - loss: 0.5483 - val_accuracy: 0.6574 - val_loss: 1.4057 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7164 - loss: 0.5845 - val_accuracy: 0.6852 - val_loss: 0.8575 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6860 - loss: 0.6050 - val_accuracy: 0.5220 - val_loss: 1.3541 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.6854 - loss: 0.6124 - val_accuracy: 0.6460 - val_loss: 1.7902 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7092 - loss: 0.5669 - val_accuracy: 0.6444 - val_loss: 1.8678 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6933 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7166 - loss: 0.5516 - val_accuracy: 0.6427 - val_loss: 1.8067 - learning_rate: 5.0000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7112 - loss: 0.5653 - val_accuracy: 0.7015 - val_loss: 0.7258 - learning_rate: 5.0000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7158 - loss: 0.5791 - val_accuracy: 0.6852 - val_loss: 0.8807 - learning_rate: 5.0000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6803 - loss: 0.6046 - val_accuracy: 0.4290 - val_loss: 2.7142 - learning_rate: 5.0000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7203 - loss: 0.5782 - val_accuracy: 0.7096 - val_loss: 0.7190 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7148 - loss: 0.5394 - val_accuracy: 0.6688 - val_loss: 0.7867 - learning_rate: 5.0000e-04
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7066 - loss: 0.5535 - val_accuracy: 0.6770 - val_loss: 1.0476 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6896 - loss: 0.5964 - val_accuracy: 0.6852 - val_loss: 0.8562 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7201 - loss: 0.5548 - val_accuracy: 0.6949 - val_loss: 0.7731 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6888 - loss: 0.5673 - val_accuracy: 0.7064 - val_loss: 0.7501 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7187 - loss: 0.5450 - val_accuracy: 0.7145 - val_loss: 0.7360 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7121 - loss: 0.5605 - val_accuracy: 0.6852 - val_loss: 0.8641 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6946 - loss: 0.5821 - val_accuracy: 0.6835 - val_loss: 0.8509 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7245 - loss: 0.5410 - val_accuracy: 0.6949 - val_loss: 0.8011 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7334 - loss: 0.5471 - val_accuracy: 0.6949 - val_loss: 0.7876 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6975 - loss: 0.5683 - val_accuracy: 0.6982 - val_loss: 0.8083 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7528 - loss: 0.5376 - val_accuracy: 0.6835 - val_loss: 0.8386 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6553 - loss: 0.6141 - val_accuracy: 0.7096 - val_loss: 0.7425 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6532 - loss: 0.6104 - val_accuracy: 0.6900 - val_loss: 0.8117 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7142 - loss: 0.5609 - val_accuracy: 0.7031 - val_loss: 0.7607 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6902 - loss: 0.5842 - val_accuracy: 0.7129 - val_loss: 0.7432 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7229 - loss: 0.5615 - val_accuracy: 0.6835 - val_loss: 0.8436 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6698 - loss: 0.5975 - val_accuracy: 0.6998 - val_loss: 0.7731 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7305 - loss: 0.5479 - val_accuracy: 0.6900 - val_loss: 0.8243 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7325 - loss: 0.5527 - val_accuracy: 0.7015 - val_loss: 0.7517 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6852 - loss: 0.5818 - val_accuracy: 0.6966 - val_loss: 0.8051 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7111 - loss: 0.5694 - val_accuracy: 0.7096 - val_loss: 0.7303 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7121 - loss: 0.5492 - val_accuracy: 0.6933 - val_loss: 0.7964 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7228 - loss: 0.5466 - val_accuracy: 0.6852 - val_loss: 0.8694 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7120 - loss: 0.5463 - val_accuracy: 0.6966 - val_loss: 0.7858 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6887 - loss: 0.5781 - val_accuracy: 0.7113 - val_loss: 0.7287 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7244 - loss: 0.5634 - val_accuracy: 0.7080 - val_loss: 0.7434 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6990 - loss: 0.5823 - val_accuracy: 0.6998 - val_loss: 0.7964 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7052 - loss: 0.5542 - val_accuracy: 0.7064 - val_loss: 0.7545 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7236 - loss: 0.5238 - val_accuracy: 0.6949 - val_loss: 0.8064 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7064 - loss: 0.5663 - val_accuracy: 0.6966 - val_loss: 0.7774 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step 

In [13]:
#ResN-12
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('linear')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('linear')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('linear')(conv_z)
    
    
    print ('build conv_w')
    conv_w = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_z)
    conv_w = keras.layers.Activation('linear')(conv_w)
     
    shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
    shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
   # shortcut_y = keras.layers.BatchNormalization()(x)    
    #shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_w])
    y = keras.layers.Activation('linear')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist12 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log12 = pd.DataFrame(hist12.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model12 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
build conv_w
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 10s 52ms/step - accuracy: 0.4953 - loss: 1.0155 - val_accuracy: 0.4290 - val_loss: 0.7732 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.5551 - loss: 0.6940 - val_accuracy: 0.3801 - val_loss: 1.1084 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.5691 - loss: 0.6875 - val_accuracy: 0.3801 - val_loss: 1.2754 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.5943 - loss: 0.6835 - val_accuracy: 0.3801 - val_loss: 2.2399 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.5701 - loss: 0.6737 - val_accuracy: 0.3883 - val_loss: 2.0664 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6198 - loss: 0.6444 - val_accuracy: 0.5383 - val_loss: 0.7474 -

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6865 - loss: 0.5935 - val_accuracy: 0.6395 - val_loss: 1.5361 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6950 - loss: 0.6043 - val_accuracy: 0.7047 - val_loss: 0.7257 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6851 - loss: 0.6075 - val_accuracy: 0.6199 - val_loss: 5.4075 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6676 - loss: 0.5884 - val_accuracy: 0.6281 - val_loss: 2.2464 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7035 - loss: 0.5721 - val_accuracy: 0.6215 - val_loss: 2.7338 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7079 - loss: 0.5716 - val_accuracy: 0.7015 - val_loss: 0.7304 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6965 - loss: 0.5821 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6843 - loss: 0.5712 - val_accuracy: 0.6852 - val_loss: 0.7286 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6801 - loss: 0.6012 - val_accuracy: 0.3915 - val_loss: 4.4850 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 31ms/step - accuracy: 0.7078 - loss: 0.5942 - val_accuracy: 0.6688 - val_loss: 1.1113 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6915 - loss: 0.5754 - val_accuracy: 0.6215 - val_loss: 3.0968 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6869 - loss: 0.5785 - val_accuracy: 0.6982 - val_loss: 0.6846 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6704 - loss: 0.5829 - val_accuracy: 0.6998 - val_loss: 0.6875 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7417 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7322 - loss: 0.5584 - val_accuracy: 0.4878 - val_loss: 1.5447 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7124 - loss: 0.5803 - val_accuracy: 0.6395 - val_loss: 1.9445 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6786 - loss: 0.5690 - val_accuracy: 0.6215 - val_loss: 3.6982 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6943 - loss: 0.5775 - val_accuracy: 0.6786 - val_loss: 0.8981 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7146 - loss: 0.5620 - val_accuracy: 0.6819 - val_loss: 0.8289 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7167 - loss: 0.5639 - val_accuracy: 0.6411 - val_loss: 1.9827 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.6755 - loss: 0.6

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7084 - loss: 0.5968 - val_accuracy: 0.6607 - val_loss: 1.3605 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6985 - loss: 0.5795 - val_accuracy: 0.6444 - val_loss: 1.7219 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6971 - loss: 0.5746 - val_accuracy: 0.7031 - val_loss: 0.7811 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7061 - loss: 0.5774 - val_accuracy: 0.4812 - val_loss: 1.6704 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6652 - loss: 0.5916 - val_accuracy: 0.5546 - val_loss: 1.2034 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7020 - loss: 0.5806 - val_accuracy: 0.6672 - val_loss: 1.0111 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7020 - loss: 0.5

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7138 - loss: 0.5536 - val_accuracy: 0.6835 - val_loss: 0.8755 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7419 - loss: 0.5312 - val_accuracy: 0.6966 - val_loss: 0.7751 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7035 - loss: 0.5717 - val_accuracy: 0.7031 - val_loss: 0.7593 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7069 - loss: 0.5470 - val_accuracy: 0.6819 - val_loss: 1.0155 - learning_rate: 1.0000e-04
Epoch 1819/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7113 - loss: 0.5681 - val_accuracy: 0.6884 - val_loss: 0.8251 - learning_rate: 1.0000e-04
Epoch 1820/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6980 - loss: 0.5638 - val_accuracy: 0.6966 - val_loss: 0.8022 - learning_rate: 1.0000e-04
Epoch 1821/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7030 - loss: 0.5665 - val_accuracy: 0.6949 - val_loss: 0.7770 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7296 - loss: 0.5410 - val_accuracy: 0.6852 - val_loss: 0.8323 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7363 - loss: 0.5354 - val_accuracy: 0.6966 - val_loss: 0.7798 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6959 - loss: 0.5763 - val_accuracy: 0.7015 - val_loss: 0.7658 - learning_rate: 1.0000e-04
Epoch 1861/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7102 - loss: 0.5576 - val_accuracy: 0.7015 - val_loss: 0.7703 - learning_rate: 1.0000e-04
Epoch 1862/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7144 - loss: 0.5605 - val_accuracy: 0.6868 - val_loss: 0.8258 - learning_rate: 1.0000e-04
Epoch 1863/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7078 - loss: 0.5934 - val_accuracy: 0.7080 - val_loss: 0.7442 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7255 - loss: 0.5776 - val_accuracy: 0.6835 - val_loss: 0.8717 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6979 - loss: 0.5663 - val_accuracy: 0.6949 - val_loss: 0.7885 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7011 - loss: 0.5575 - val_accuracy: 0.6949 - val_loss: 0.7835 - learning_rate: 1.0000e-04
Epoch 1903/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7247 - loss: 0.5423 - val_accuracy: 0.7031 - val_loss: 0.7756 - learning_rate: 1.0000e-04
Epoch 1904/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7021 - loss: 0.5677 - val_accuracy: 0.6998 - val_loss: 0.7752 - learning_rate: 1.0000e-04
Epoch 1905/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7019 - loss: 0.5659 - val_accuracy: 0.7015 - val_loss: 0.7715 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7082 - loss: 0.5508 - val_accuracy: 0.6835 - val_loss: 0.8787 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7125 - loss: 0.5666 - val_accuracy: 0.7031 - val_loss: 0.7676 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6896 - loss: 0.5407 - val_accuracy: 0.7113 - val_loss: 0.7501 - learning_rate: 1.0000e-04
Epoch 1945/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7088 - loss: 0.5640 - val_accuracy: 0.6966 - val_loss: 0.7889 - learning_rate: 1.0000e-04
Epoch 1946/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6966 - loss: 0.5773 - val_accuracy: 0.7031 - val_loss: 0.7713 - learning_rate: 1.0000e-04
Epoch 1947/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6905 - loss: 0.5597 - val_accuracy: 0.6949 - val_loss: 0.8016 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6977 - loss: 0.5754 - val_accuracy: 0.6966 - val_loss: 0.7866 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6926 - loss: 0.5430 - val_accuracy: 0.6966 - val_loss: 0.8025 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7286 - loss: 0.5455 - val_accuracy: 0.6966 - val_loss: 0.8031 - learning_rate: 1.0000e-04
Epoch 1987/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7274 - loss: 0.5461 - val_accuracy: 0.6835 - val_loss: 0.8511 - learning_rate: 1.0000e-04
Epoch 1988/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6977 - loss: 0.5501 - val_accuracy: 0.7031 - val_loss: 0.7633 - learning_rate: 1.0000e-04
Epoch 1989/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step 

In [14]:
#ResN-13
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('linear')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('linear')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('linear')(conv_z)
    
    
    #shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
    #shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
    shortcut_y = keras.layers.BatchNormalization()(x)    
    #shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_z])
    y = keras.layers.Activation('linear')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist13 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log13 = pd.DataFrame(hist13.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model13 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 6s 38ms/step - accuracy: 0.5129 - loss: 0.7406 - val_accuracy: 0.6199 - val_loss: 0.6664 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.5476 - loss: 0.6922 - val_accuracy: 0.6199 - val_loss: 0.8122 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.5478 - loss: 0.6918 - val_accuracy: 0.4388 - val_loss: 0.7353 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5513 - loss: 0.6878 - val_accuracy: 0.6199 - val_loss: 1.0715 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.5677 - loss: 0.6849 - val_accuracy: 0.6199 - val_loss: 0.6563 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.5729 - loss: 0.6792 - val_accuracy: 0.3801 - val_loss: 1.9270 - learning_rate

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6906 - loss: 0.5973 - val_accuracy: 0.6313 - val_loss: 1.9708 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6824 - loss: 0.5861 - val_accuracy: 0.6199 - val_loss: 3.0607 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.6861 - loss: 0.6169 - val_accuracy: 0.6884 - val_loss: 0.7952 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7203 - loss: 0.5738 - val_accuracy: 0.6998 - val_loss: 0.7156 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6649 - loss: 0.6284 - val_accuracy: 0.6525 - val_loss: 1.8394 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7359 - loss: 0.5665 - val_accuracy: 0.5546 - val_loss: 1.0780 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.7118 - loss: 0.5713 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7294 - loss: 0.5522 - val_accuracy: 0.6770 - val_loss: 0.9087 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7233 - loss: 0.5772 - val_accuracy: 0.6835 - val_loss: 0.8110 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7051 - loss: 0.5862 - val_accuracy: 0.6607 - val_loss: 1.4199 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6926 - loss: 0.6090 - val_accuracy: 0.4356 - val_loss: 2.4703 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7017 - loss: 0.5725 - val_accuracy: 0.6672 - val_loss: 1.0440 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6899 - loss: 0.5898 - val_accuracy: 0.6998 - val_loss: 0.7931 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7228 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6963 - loss: 0.5926 - val_accuracy: 0.6852 - val_loss: 0.8541 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.6669 - loss: 0.6072 - val_accuracy: 0.6998 - val_loss: 0.7777 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7002 - loss: 0.5626 - val_accuracy: 0.4763 - val_loss: 1.7798 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7106 - loss: 0.5559 - val_accuracy: 0.6639 - val_loss: 1.1799 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7069 - loss: 0.5755 - val_accuracy: 0.6819 - val_loss: 0.8052 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7137 - loss: 0.5558 - val_accuracy: 0.6819 - val_loss: 0.9647 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7001 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6927 - loss: 0.5674 - val_accuracy: 0.7047 - val_loss: 0.7597 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7003 - loss: 0.5722 - val_accuracy: 0.7113 - val_loss: 0.7093 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.6831 - loss: 0.5977 - val_accuracy: 0.6884 - val_loss: 0.8674 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7407 - loss: 0.5451 - val_accuracy: 0.6917 - val_loss: 0.7262 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7025 - loss: 0.5768 - val_accuracy: 0.6525 - val_loss: 1.5576 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7433 - loss: 0.5540 - val_accuracy: 0.6852 - val_loss: 0.8518 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7007 - loss: 0.5

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.6962 - loss: 0.5550 - val_accuracy: 0.6966 - val_loss: 0.8110 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7010 - loss: 0.5561 - val_accuracy: 0.6835 - val_loss: 0.8561 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6919 - loss: 0.5668 - val_accuracy: 0.6949 - val_loss: 0.7872 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7161 - loss: 0.5633 - val_accuracy: 0.6949 - val_loss: 0.7833 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7097 - loss: 0.5465 - val_accuracy: 0.6998 - val_loss: 0.7777 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7105 - loss: 0.5591 - val_accuracy: 0.7031 - val_loss: 0.7599 - learning_rate: 1.0000e-04
Epoch 1819/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7289 - loss: 0.5308 - val_accuracy: 0.6819 - val_loss: 0.8393 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6842 - loss: 0.5988 - val_accuracy: 0.6949 - val_loss: 0.7746 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7215 - loss: 0.5627 - val_accuracy: 0.6949 - val_loss: 0.7941 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7278 - loss: 0.5547 - val_accuracy: 0.6949 - val_loss: 0.8212 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7265 - loss: 0.5442 - val_accuracy: 0.7064 - val_loss: 0.7503 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7010 - loss: 0.5706 - val_accuracy: 0.6900 - val_loss: 0.8143 - learning_rate: 1.0000e-04
Epoch 1861/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7211 - loss: 0.5513 - val_accuracy: 0.7031 - val_loss: 0.7632 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7165 - loss: 0.5586 - val_accuracy: 0.6949 - val_loss: 0.7930 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6895 - loss: 0.5685 - val_accuracy: 0.6933 - val_loss: 0.8133 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7013 - loss: 0.5881 - val_accuracy: 0.6966 - val_loss: 0.8016 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7086 - loss: 0.5594 - val_accuracy: 0.6917 - val_loss: 0.8192 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.6826 - loss: 0.5823 - val_accuracy: 0.6949 - val_loss: 0.7837 - learning_rate: 1.0000e-04
Epoch 1903/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.6990 - loss: 0.5601 - val_accuracy: 0.6933 - val_loss: 0.7955 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7518 - loss: 0.5135 - val_accuracy: 0.6966 - val_loss: 0.8098 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7155 - loss: 0.5459 - val_accuracy: 0.7031 - val_loss: 0.7655 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7037 - loss: 0.5507 - val_accuracy: 0.6966 - val_loss: 0.7777 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7273 - loss: 0.5497 - val_accuracy: 0.6966 - val_loss: 0.8069 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7101 - loss: 0.5656 - val_accuracy: 0.7031 - val_loss: 0.7646 - learning_rate: 1.0000e-04
Epoch 1945/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6928 - loss: 0.5929 - val_accuracy: 0.6982 - val_loss: 0.7918 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7075 - loss: 0.5506 - val_accuracy: 0.6966 - val_loss: 0.8062 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6945 - loss: 0.5576 - val_accuracy: 0.7080 - val_loss: 0.7474 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7087 - loss: 0.5742 - val_accuracy: 0.6982 - val_loss: 0.8066 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7011 - loss: 0.5612 - val_accuracy: 0.6900 - val_loss: 0.8255 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7219 - loss: 0.5679 - val_accuracy: 0.6966 - val_loss: 0.8009 - learning_rate: 1.0000e-04
Epoch 1987/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step 

In [15]:
#ResN-14
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('linear')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('linear')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('linear')(conv_z)
    
    print ('build conv_w')
    conv_w = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_z)
    conv_w = keras.layers.Activation('linear')(conv_w)
     
    #shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
   # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
    shortcut_y = keras.layers.BatchNormalization()(x)    
    #shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_w])
    y = keras.layers.Activation('linear')(y)
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist14 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log14 = pd.DataFrame(hist14.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model14 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
build conv_w
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 4s 29ms/step - accuracy: 0.5357 - loss: 0.8411 - val_accuracy: 0.6199 - val_loss: 1.8696 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.5328 - loss: 0.6959 - val_accuracy: 0.6199 - val_loss: 2.4332 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.5241 - loss: 0.7120 - val_accuracy: 0.6199 - val_loss: 0.7773 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.5761 - loss: 0.6858 - val_accuracy: 0.6199 - val_loss: 1.2829 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.5610 - loss: 0.6890 - val_accuracy: 0.5073 - val_loss: 0.7059 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.5540 - loss: 0.6906 - val_accuracy: 0.3931 - val_loss: 0.9416 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6771 - loss: 0.6175 - val_accuracy: 0.6378 - val_loss: 1.7680 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7399 - loss: 0.5620 - val_accuracy: 0.7064 - val_loss: 0.6195 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6981 - loss: 0.5893 - val_accuracy: 0.6982 - val_loss: 0.7186 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6802 - loss: 0.5741 - val_accuracy: 0.6786 - val_loss: 0.9335 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.7188 - loss: 0.5814 - val_accuracy: 0.7064 - val_loss: 0.6662 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6977 - loss: 0.5867 - val_accuracy: 0.4698 - val_loss: 1.5592 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7206 - loss: 0.5506 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6990 - loss: 0.5717 - val_accuracy: 0.7015 - val_loss: 0.7365 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7404 - loss: 0.5564 - val_accuracy: 0.5856 - val_loss: 1.0138 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7009 - loss: 0.5760 - val_accuracy: 0.6476 - val_loss: 1.8671 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7265 - loss: 0.5602 - val_accuracy: 0.7064 - val_loss: 0.7279 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7157 - loss: 0.5787 - val_accuracy: 0.6411 - val_loss: 1.7324 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7294 - loss: 0.5693 - val_accuracy: 0.6525 - val_loss: 0.8784 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7064 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7237 - loss: 0.5522 - val_accuracy: 0.7096 - val_loss: 0.7168 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7119 - loss: 0.5854 - val_accuracy: 0.6003 - val_loss: 0.9795 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7099 - loss: 0.5651 - val_accuracy: 0.5449 - val_loss: 1.2334 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7240 - loss: 0.5694 - val_accuracy: 0.5220 - val_loss: 1.2833 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7075 - loss: 0.5780 - val_accuracy: 0.6427 - val_loss: 0.9131 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7325 - loss: 0.5638 - val_accuracy: 0.7047 - val_loss: 0.7122 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7132 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6907 - loss: 0.5747 - val_accuracy: 0.6949 - val_loss: 0.7740 - learning_rate: 5.0000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7057 - loss: 0.5581 - val_accuracy: 0.6591 - val_loss: 1.2425 - learning_rate: 5.0000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7309 - loss: 0.5608 - val_accuracy: 0.7145 - val_loss: 0.7209 - learning_rate: 5.0000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7190 - loss: 0.5711 - val_accuracy: 0.6656 - val_loss: 1.1272 - learning_rate: 5.0000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7442 - loss: 0.5467 - val_accuracy: 0.6835 - val_loss: 0.8423 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7087 - loss: 0.5778 - val_accuracy: 0.7015 - val_loss: 0.7520 - learning_rate: 5.0000e-04
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6817 - loss: 0.5740 - val_accuracy: 0.6917 - val_loss: 0.8101 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6749 - loss: 0.5664 - val_accuracy: 0.6982 - val_loss: 0.7822 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7013 - loss: 0.5522 - val_accuracy: 0.6835 - val_loss: 0.8733 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7046 - loss: 0.6037 - val_accuracy: 0.6884 - val_loss: 0.8152 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7098 - loss: 0.5427 - val_accuracy: 0.6949 - val_loss: 0.7861 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7072 - loss: 0.5481 - val_accuracy: 0.6966 - val_loss: 0.7807 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6924 - loss: 0.5782 - val_accuracy: 0.6949 - val_loss: 0.7978 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7287 - loss: 0.5404 - val_accuracy: 0.6966 - val_loss: 0.8160 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6898 - loss: 0.5667 - val_accuracy: 0.6966 - val_loss: 0.7798 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7242 - loss: 0.5507 - val_accuracy: 0.6835 - val_loss: 0.8630 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7238 - loss: 0.5444 - val_accuracy: 0.7031 - val_loss: 0.7631 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7177 - loss: 0.5652 - val_accuracy: 0.6949 - val_loss: 0.7903 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7256 - loss: 0.5293 - val_accuracy: 0.6900 - val_loss: 0.8308 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7319 - loss: 0.5284 - val_accuracy: 0.6982 - val_loss: 0.7835 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7083 - loss: 0.5519 - val_accuracy: 0.6966 - val_loss: 0.8040 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7112 - loss: 0.5805 - val_accuracy: 0.6949 - val_loss: 0.7777 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7339 - loss: 0.5539 - val_accuracy: 0.6933 - val_loss: 0.7888 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6877 - loss: 0.5750 - val_accuracy: 0.6835 - val_loss: 0.8385 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7054 - loss: 0.5437 - val_accuracy: 0.6966 - val_loss: 0.8066 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7019 - loss: 0.5546 - val_accuracy: 0.6949 - val_loss: 0.7906 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6761 - loss: 0.5619 - val_accuracy: 0.7015 - val_loss: 0.7684 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7352 - loss: 0.5323 - val_accuracy: 0.7015 - val_loss: 0.7664 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6883 - loss: 0.5950 - val_accuracy: 0.6868 - val_loss: 0.8200 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7153 - loss: 0.5495 - val_accuracy: 0.6966 - val_loss: 0.8165 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6982 - loss: 0.5741 - val_accuracy: 0.6966 - val_loss: 0.7956 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7179 - loss: 0.5708 - val_accuracy: 0.6819 - val_loss: 0.8676 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7269 - loss: 0.5555 - val_accuracy: 0.6966 - val_loss: 0.7948 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6864 - loss: 0.5777 - val_accuracy: 0.6819 - val_loss: 0.8371 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6954 - loss: 0.5559 - val_accuracy: 0.6835 - val_loss: 0.9006 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7019 - loss: 0.5809 - val_accuracy: 0.6966 - val_loss: 0.7781 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step 

In [16]:
#ResN-15
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('linear')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('linear')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('linear')(conv_z)
    
    
    #shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
    #shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
   # shortcut_y = keras.layers.BatchNormalization()(x)    
    shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_z])
    y = keras.layers.Activation('linear')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist15 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log15 = pd.DataFrame(hist15.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model15 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 7s 65ms/step - accuracy: 0.5098 - loss: 0.7040 - val_accuracy: 0.6199 - val_loss: 2.4933 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.4990 - loss: 0.7184 - val_accuracy: 0.6199 - val_loss: 1.2605 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.5402 - loss: 0.6889 - val_accuracy: 0.6199 - val_loss: 0.8091 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5405 - loss: 0.6848 - val_accuracy: 0.6199 - val_loss: 1.5459 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6517 - loss: 0.6375 - val_accuracy: 0.6199 - val_loss: 5.0754 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6086 - loss: 0.7098 - val_accuracy: 0.6966 - val_loss: 0.6034 - learning_rate

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.6947 - loss: 0.5884 - val_accuracy: 0.7015 - val_loss: 0.6982 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7161 - loss: 0.5760 - val_accuracy: 0.6639 - val_loss: 1.0544 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7212 - loss: 0.5909 - val_accuracy: 0.6982 - val_loss: 0.7437 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7018 - loss: 0.5770 - val_accuracy: 0.5383 - val_loss: 1.0952 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7421 - loss: 0.5489 - val_accuracy: 0.5041 - val_loss: 1.2473 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7225 - loss: 0.5863 - val_accuracy: 0.6199 - val_loss: 4.1883 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6771 - loss: 0.6345 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7125 - loss: 0.5627 - val_accuracy: 0.5139 - val_loss: 1.2634 - learning_rate: 0.0010
Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7337 - loss: 0.5711 - val_accuracy: 0.6427 - val_loss: 1.9660 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7133 - loss: 0.5509 - val_accuracy: 0.4943 - val_loss: 1.4370 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6875 - loss: 0.5842 - val_accuracy: 0.6330 - val_loss: 2.6410 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6998 - loss: 0.5809 - val_accuracy: 0.4682 - val_loss: 1.6775 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7035 - loss: 0.5729 - val_accuracy: 0.6982 - val_loss: 0.7456 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7085 - loss: 0.5856 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7051 - loss: 0.5728 - val_accuracy: 0.6754 - val_loss: 0.9545 - learning_rate: 0.0010
Epoch 131/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7353 - loss: 0.5581 - val_accuracy: 0.6786 - val_loss: 0.9645 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7329 - loss: 0.5469 - val_accuracy: 0.6427 - val_loss: 1.8343 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7541 - loss: 0.5550 - val_accuracy: 0.6900 - val_loss: 0.7463 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7147 - loss: 0.5477 - val_accuracy: 0.6623 - val_loss: 1.2164 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6822 - loss: 0.5938 - val_accuracy: 0.6786 - val_loss: 0.9914 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7118 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7173 - loss: 0.5637 - val_accuracy: 0.6917 - val_loss: 0.7950 - learning_rate: 5.0000e-04
Epoch 174/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7040 - loss: 0.5730 - val_accuracy: 0.6623 - val_loss: 0.8354 - learning_rate: 5.0000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7119 - loss: 0.5839 - val_accuracy: 0.7096 - val_loss: 0.7298 - learning_rate: 5.0000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7282 - loss: 0.5333 - val_accuracy: 0.6672 - val_loss: 1.2383 - learning_rate: 5.0000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7285 - loss: 0.5546 - val_accuracy: 0.6688 - val_loss: 1.0945 - learning_rate: 5.0000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6893 - loss: 0.5808 - val_accuracy: 0.6476 - val_loss: 1.7004 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6837 - loss: 0.5658 - val_accuracy: 0.6852 - val_loss: 0.8627 - learning_rate: 1.0000e-04
Epoch 1812/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6997 - loss: 0.5700 - val_accuracy: 0.7031 - val_loss: 0.7567 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6916 - loss: 0.5566 - val_accuracy: 0.6966 - val_loss: 0.7795 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7333 - loss: 0.5234 - val_accuracy: 0.7113 - val_loss: 0.7340 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7391 - loss: 0.5252 - val_accuracy: 0.6770 - val_loss: 0.9450 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7055 - loss: 0.5596 - val_accuracy: 0.6966 - val_loss: 0.8059 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7023 - loss: 0.5892 - val_accuracy: 0.6966 - val_loss: 0.7783 - learning_rate: 1.0000e-04
Epoch 1854/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7125 - loss: 0.5570 - val_accuracy: 0.6949 - val_loss: 0.7924 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7188 - loss: 0.5501 - val_accuracy: 0.6852 - val_loss: 0.8636 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6853 - loss: 0.5745 - val_accuracy: 0.6949 - val_loss: 0.7927 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7216 - loss: 0.5554 - val_accuracy: 0.7031 - val_loss: 0.7631 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6976 - loss: 0.5546 - val_accuracy: 0.6949 - val_loss: 0.7952 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7064 - loss: 0.5664 - val_accuracy: 0.6852 - val_loss: 0.8492 - learning_rate: 1.0000e-04
Epoch 1896/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6750 - loss: 0.5776 - val_accuracy: 0.6852 - val_loss: 0.8472 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7190 - loss: 0.5503 - val_accuracy: 0.6803 - val_loss: 0.9137 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7437 - loss: 0.5334 - val_accuracy: 0.6917 - val_loss: 0.8206 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7022 - loss: 0.5665 - val_accuracy: 0.7064 - val_loss: 0.7507 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7097 - loss: 0.5395 - val_accuracy: 0.7064 - val_loss: 0.7522 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 36ms/step - accuracy: 0.6818 - loss: 0.5645 - val_accuracy: 0.6786 - val_loss: 0.9049 - learning_rate: 1.0000e-04
Epoch 1938/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7620 - loss: 0.5155 - val_accuracy: 0.7031 - val_loss: 0.7779 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7202 - loss: 0.5485 - val_accuracy: 0.7129 - val_loss: 0.7380 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7257 - loss: 0.5577 - val_accuracy: 0.6835 - val_loss: 0.8673 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6722 - loss: 0.6140 - val_accuracy: 0.6803 - val_loss: 0.8363 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7189 - loss: 0.5483 - val_accuracy: 0.7031 - val_loss: 0.7616 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7107 - loss: 0.5673 - val_accuracy: 0.7096 - val_loss: 0.7453 - learning_rate: 1.0000e-04
Epoch 1980/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7271 - loss: 0.5511 - val_accuracy: 0.6852 - val_loss: 0.8498 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7216 - loss: 0.5418 - val_accuracy: 0.7080 - val_loss: 0.7414 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7106 - loss: 0.5494 - val_accuracy: 0.6966 - val_loss: 0.7954 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6774 - loss: 0.5959 - val_accuracy: 0.6835 - val_loss: 0.8442 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7035 - loss: 0.5663 - val_accuracy: 0.6819 - val_loss: 0.8345 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

In [17]:
#ResN-16
# %load ResNet.py
#!/usr/bin/env python3
"""
Created on Sat Nov 12 01:09:17 2016

@author: stephen
"""

from tensorflow import keras
import numpy as np
import pandas as pd

np.random.seed(813306)
 
def build_resnet(input_shape, n_feature_maps, nb_classes):
    print ('build conv_x')
    x = keras.layers.Input(shape=(input_shape))
    conv_x = keras.layers.Conv2D(n_feature_maps, 8, 1, padding='same')(x)
    conv_x = keras.layers.Activation('linear')(conv_x)
     
    print ('build conv_y')
    conv_y = keras.layers.Conv2D(n_feature_maps, 5, 1, padding='same')(conv_x)
    conv_y = keras.layers.Activation('linear')(conv_y)
     
    print ('build conv_z')
    conv_z = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_y)
    conv_z = keras.layers.Activation('linear')(conv_z)
    
    print ('build conv_w')
    conv_w = keras.layers.Conv2D(n_feature_maps, 3, 1, padding='same')(conv_z)
    conv_w = keras.layers.Activation('linear')(conv_w)
     
    #shortcut_y = keras.layers.Conv2D(n_feature_maps, 1, 1,padding='same')(x)
   # shortcut_y = keras.layers.BatchNormalization()(shortcut_y)
   # shortcut_y = keras.layers.BatchNormalization()(x)    
    shortcut_y = x 
    print ('Merging skip connection')
    y = keras.layers.Add()([shortcut_y, conv_w])
    y = keras.layers.Activation('linear')(y)
     
  
     
    full = keras.layers.GlobalAveragePooling2D()(y)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    print ('        -- model was built.')
    return x, out
 
 
 
       
def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y


 
 
#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
     
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
     
     
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
     
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
      
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))
     
     
    x , y = build_resnet(x_train.shape[1:], 128, nb_classes)
    model = keras.models.Model(inputs=x, outputs=y)
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
      
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor='loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#    early_stop=keras.callbacks.EarlyStopping(monitor='val_acc',min_delta=0.3,patience=50,verbose=0,mode='auto')

#numbering
    hist16 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

    #numbering
    log16 = pd.DataFrame(hist16.history)
   # print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])
    
import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
res_model16 = keras.models.load_model(model_h5_file)

build conv_x
build conv_y
build conv_z
build conv_w
Merging skip connection
        -- model was built.
Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 8s 57ms/step - accuracy: 0.5024 - loss: 0.7330 - val_accuracy: 0.6199 - val_loss: 0.9019 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.5359 - loss: 0.6938 - val_accuracy: 0.6199 - val_loss: 2.0079 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6022 - loss: 0.6821 - val_accuracy: 0.6199 - val_loss: 0.6678 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.5670 - loss: 0.6836 - val_accuracy: 0.3801 - val_loss: 1.6439 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.5613 - loss: 0.6884 - val_accuracy: 0.6199 - val_loss: 2.6457 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.5735 - loss: 0.6769 - val_accuracy: 0.6199 - val_loss: 1.2185 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7046 - loss: 0.6116 - val_accuracy: 0.6411 - val_loss: 1.7528 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7292 - loss: 0.5712 - val_accuracy: 0.6639 - val_loss: 1.0897 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7266 - loss: 0.5750 - val_accuracy: 0.6427 - val_loss: 1.9941 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7309 - loss: 0.5533 - val_accuracy: 0.6591 - val_loss: 0.7858 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7255 - loss: 0.5681 - val_accuracy: 0.6623 - val_loss: 1.1317 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7128 - loss: 0.5695 - val_accuracy: 0.6966 - val_loss: 0.7869 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6774 - loss: 0.5987 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7158 - loss: 0.5495 - val_accuracy: 0.6623 - val_loss: 1.2549 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6996 - loss: 0.5692 - val_accuracy: 0.6313 - val_loss: 3.0718 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6742 - loss: 0.6447 - val_accuracy: 0.5449 - val_loss: 1.2717 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6914 - loss: 0.6126 - val_accuracy: 0.6672 - val_loss: 1.3056 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7302 - loss: 0.5491 - val_accuracy: 0.6933 - val_loss: 0.7191 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7128 - loss: 0.5676 - val_accuracy: 0.6330 - val_loss: 2.5123 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7094 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7487 - loss: 0.5591 - val_accuracy: 0.6558 - val_loss: 1.4260 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7030 - loss: 0.5740 - val_accuracy: 0.6607 - val_loss: 1.3360 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6963 - loss: 0.5911 - val_accuracy: 0.6607 - val_loss: 1.3427 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6615 - loss: 0.6212 - val_accuracy: 0.6900 - val_loss: 0.8340 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7195 - loss: 0.5713 - val_accuracy: 0.5693 - val_loss: 1.0835 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6954 - loss: 0.5654 - val_accuracy: 0.6607 - val_loss: 0.8269 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7230 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7289 - loss: 0.5683 - val_accuracy: 0.6656 - val_loss: 1.1568 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7449 - loss: 0.5399 - val_accuracy: 0.6721 - val_loss: 0.7683 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7250 - loss: 0.5526 - val_accuracy: 0.6688 - val_loss: 1.0514 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7302 - loss: 0.5624 - val_accuracy: 0.3948 - val_loss: 4.1472 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6747 - loss: 0.5972 - val_accuracy: 0.6378 - val_loss: 2.3068 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7044 - loss: 0.5825 - val_accuracy: 0.6998 - val_loss: 0.7436 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7006 - loss: 0.6

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7087 - loss: 0.5796 - val_accuracy: 0.6868 - val_loss: 0.8256 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7019 - loss: 0.5790 - val_accuracy: 0.6949 - val_loss: 0.7866 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6913 - loss: 0.5807 - val_accuracy: 0.6868 - val_loss: 0.8483 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7287 - loss: 0.5396 - val_accuracy: 0.7096 - val_loss: 0.7470 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6748 - loss: 0.5896 - val_accuracy: 0.6933 - val_loss: 0.8160 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6908 - loss: 0.5821 - val_accuracy: 0.6770 - val_loss: 0.9887 - learning_rate: 1.0000e-04
Epoch 1819/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7158 - loss: 0.5748 - val_accuracy: 0.7047 - val_loss: 0.7551 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7142 - loss: 0.5470 - val_accuracy: 0.6868 - val_loss: 0.8389 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6940 - loss: 0.5703 - val_accuracy: 0.6966 - val_loss: 0.7978 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7253 - loss: 0.5320 - val_accuracy: 0.6884 - val_loss: 0.8325 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7027 - loss: 0.5715 - val_accuracy: 0.6949 - val_loss: 0.7994 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7353 - loss: 0.5535 - val_accuracy: 0.6966 - val_loss: 0.7983 - learning_rate: 1.0000e-04
Epoch 1861/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.7098 - loss: 0.5730 - val_accuracy: 0.6803 - val_loss: 0.8359 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7243 - loss: 0.5640 - val_accuracy: 0.6884 - val_loss: 0.8299 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7042 - loss: 0.5663 - val_accuracy: 0.6966 - val_loss: 0.7813 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7323 - loss: 0.5349 - val_accuracy: 0.7031 - val_loss: 0.7612 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7068 - loss: 0.5733 - val_accuracy: 0.7031 - val_loss: 0.7554 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7137 - loss: 0.5645 - val_accuracy: 0.6819 - val_loss: 0.8400 - learning_rate: 1.0000e-04
Epoch 1903/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.6626 - loss: 0.5947 - val_accuracy: 0.6835 - val_loss: 0.8668 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7608 - loss: 0.5376 - val_accuracy: 0.6819 - val_loss: 0.8425 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6979 - loss: 0.5711 - val_accuracy: 0.6835 - val_loss: 0.8484 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6837 - loss: 0.5672 - val_accuracy: 0.6949 - val_loss: 0.7906 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6880 - loss: 0.6053 - val_accuracy: 0.6966 - val_loss: 0.8062 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7057 - loss: 0.5451 - val_accuracy: 0.7031 - val_loss: 0.7782 - learning_rate: 1.0000e-04
Epoch 1945/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7128 - loss: 0.5683 - val_accuracy: 0.6933 - val_loss: 0.7856 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7205 - loss: 0.5534 - val_accuracy: 0.6884 - val_loss: 0.8303 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7220 - loss: 0.5388 - val_accuracy: 0.6949 - val_loss: 0.8015 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7170 - loss: 0.5658 - val_accuracy: 0.7178 - val_loss: 0.7348 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7181 - loss: 0.5811 - val_accuracy: 0.6819 - val_loss: 0.8321 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6963 - loss: 0.5669 - val_accuracy: 0.6835 - val_loss: 0.8673 - learning_rate: 1.0000e-04
Epoch 1987/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step 

In [18]:
def performance_j(list_1,list_2,int_a,int_b):
    m1 = min(list_1[int_a:int_b])
    m2 = min(list_2[int_a:int_b])
    
    ave_1 = sum(list_1[int_a:int_b])/len(list_1[int_a:int_b])
    ave_2 = sum(list_2[int_a:int_b])/len(list_2[int_a:int_b])
    
    sd_1 = np.sqrt(sum((x-ave_1)**2 for x in list_1[int_a:int_b])/len(list_1[int_a:int_b]))
    sd_2 = np.sqrt(sum((x-ave_2)**2 for x in list_2[int_a:int_b])/len(list_2[int_a:int_b]))
        
    if (ave_1-sd_1)<(ave_2-sd_2): 
        return [(ave_1-sd_1),(ave_2-sd_2),(ave_1-sd_1)]
    else:
        return [(ave_1-sd_1),(ave_2-sd_2),(ave_2-sd_2)]

In [19]:
def performance_k(list_1,list_2,int_a,int_b):
    m1 = min(list_1[int_a:int_b])
    m2 = min(list_2[int_a:int_b])
    
    ave_1 = sum(list_1[int_a:int_b])/len(list_1[int_a:int_b])
    ave_2 = sum(list_2[int_a:int_b])/len(list_2[int_a:int_b])
    
    sd_1 = np.sqrt(sum((x-ave_1)**2 for x in list_1[int_a:int_b])/len(list_1[int_a:int_b]))
    sd_2 = np.sqrt(sum((x-ave_2)**2 for x in list_2[int_a:int_b])/len(list_2[int_a:int_b]))
        
    if (ave_1-sd_1)<(ave_2-sd_2): 
        return [m1,m2,min(m1,m2)]
    else:
        return [m1,m2,min(m1,m2)]

In [20]:
perf1=[]
perf2=[]
perf3=[]
perf4=[]
perf5=[]
perf6=[]
perf7=[]
perf8=[]
perf9=[]
perf10=[]
perf11=[]
perf12=[]
perf13=[]
perf14=[]
perf15=[]
perf16=[]

for i in range(5):
    a1=performance_j(hist1.history['accuracy'],hist1.history['val_accuracy'],1500+i*100,1600+i*100)
    a2=performance_j(hist2.history['accuracy'],hist2.history['val_accuracy'],1500+i*100,1600+i*100)
    a3=performance_j(hist3.history['accuracy'],hist3.history['val_accuracy'],1500+i*100,1600+i*100)
    a4=performance_j(hist4.history['accuracy'],hist4.history['val_accuracy'],1500+i*100,1600+i*100)
    a5=performance_j(hist5.history['accuracy'],hist5.history['val_accuracy'],1500+i*100,1600+i*100)
    a6=performance_j(hist6.history['accuracy'],hist6.history['val_accuracy'],1500+i*100,1600+i*100)
    a7=performance_j(hist7.history['accuracy'],hist7.history['val_accuracy'],1500+i*100,1600+i*100)
    a8=performance_j(hist8.history['accuracy'],hist8.history['val_accuracy'],1500+i*100,1600+i*100)
    a9=performance_j(hist9.history['accuracy'],hist9.history['val_accuracy'],1500+i*100,1600+i*100)
    a10=performance_j(hist10.history['accuracy'],hist10.history['val_accuracy'],1500+i*100,1600+i*100)
    a11=performance_j(hist11.history['accuracy'],hist11.history['val_accuracy'],1500+i*100,1600+i*100)
    a12=performance_j(hist12.history['accuracy'],hist12.history['val_accuracy'],1500+i*100,1600+i*100)
    a13=performance_j(hist13.history['accuracy'],hist13.history['val_accuracy'],1500+i*100,1600+i*100)
    a14=performance_j(hist14.history['accuracy'],hist14.history['val_accuracy'],1500+i*100,1600+i*100)
    a15=performance_j(hist15.history['accuracy'],hist15.history['val_accuracy'],1500+i*100,1600+i*100)
    a16=performance_j(hist16.history['accuracy'],hist16.history['val_accuracy'],1500+i*100,1600+i*100)

    perf1 = perf1+a1
    perf2 = perf2+a2
    perf3 = perf3+a3
    perf4 = perf4+a4
    perf5 = perf5+a5
    perf6 = perf6+a6
    perf7 = perf7+a7
    perf8 = perf8+a8
    perf9 = perf9+a9
    perf10 = perf10+a10
    perf11 = perf11+a11
    perf12 = perf12+a12
    perf13 = perf13+a13
    perf14 = perf14+a14
    perf15 = perf15+a15
    perf16 = perf16+a16
    
PERF=[perf1,perf2,perf3,perf4,perf5,perf6,perf7,perf8,perf9,
perf10,perf11,perf12,perf13,perf14,perf15,perf16]   

dataframe =pd.DataFrame(PERF)
dataframe.to_csv("ReN_perf_j_trial6.csv",header=False,index=False)

In [21]:
perf1=[]
perf2=[]
perf3=[]
perf4=[]
perf5=[]
perf6=[]
perf7=[]
perf8=[]
perf9=[]
perf10=[]
perf11=[]
perf12=[]
perf13=[]
perf14=[]
perf15=[]
perf16=[]

for i in range(5):
    a1=performance_k(hist1.history['accuracy'],hist1.history['val_accuracy'],1500+i*100,1600+i*100)
    a2=performance_k(hist2.history['accuracy'],hist2.history['val_accuracy'],1500+i*100,1600+i*100)
    a3=performance_k(hist3.history['accuracy'],hist3.history['val_accuracy'],1500+i*100,1600+i*100)
    a4=performance_k(hist4.history['accuracy'],hist4.history['val_accuracy'],1500+i*100,1600+i*100)
    a5=performance_k(hist5.history['accuracy'],hist5.history['val_accuracy'],1500+i*100,1600+i*100)
    a6=performance_k(hist6.history['accuracy'],hist6.history['val_accuracy'],1500+i*100,1600+i*100)
    a7=performance_k(hist7.history['accuracy'],hist7.history['val_accuracy'],1500+i*100,1600+i*100)
    a8=performance_k(hist8.history['accuracy'],hist8.history['val_accuracy'],1500+i*100,1600+i*100)
    a9=performance_k(hist9.history['accuracy'],hist9.history['val_accuracy'],1500+i*100,1600+i*100)
    a10=performance_k(hist10.history['accuracy'],hist10.history['val_accuracy'],1500+i*100,1600+i*100)
    a11=performance_k(hist11.history['accuracy'],hist11.history['val_accuracy'],1500+i*100,1600+i*100)
    a12=performance_k(hist12.history['accuracy'],hist12.history['val_accuracy'],1500+i*100,1600+i*100)
    a13=performance_k(hist13.history['accuracy'],hist13.history['val_accuracy'],1500+i*100,1600+i*100)
    a14=performance_k(hist14.history['accuracy'],hist14.history['val_accuracy'],1500+i*100,1600+i*100)
    a15=performance_k(hist15.history['accuracy'],hist15.history['val_accuracy'],1500+i*100,1600+i*100)
    a16=performance_k(hist16.history['accuracy'],hist16.history['val_accuracy'],1500+i*100,1600+i*100)


    perf1 = perf1+a1
    perf2 = perf2+a2
    perf3 = perf3+a3
    perf4 = perf4+a4
    perf5 = perf5+a5
    perf6 = perf6+a6
    perf7 = perf7+a7
    perf8 = perf8+a8
    perf9 = perf9+a9
    perf10 = perf10+a10
    perf11 = perf11+a11
    perf12 = perf12+a12
    perf13 = perf13+a13
    perf14 = perf14+a14
    perf15 = perf15+a15
    perf16 = perf16+a16
    
PERF=[perf1,perf2,perf3,perf4,perf5,perf6,perf7,perf8,perf9,
perf10,perf11,perf12,perf13,perf14,perf15,perf16]   

dataframe =pd.DataFrame(PERF)
dataframe.to_csv("s&p500_ReN_perf_k_trial6.csv",header=False,index=False)

In [22]:
import csv

# Define the lists
tr1 = hist1.history['accuracy']
te1 = hist1.history['val_accuracy']
tr2 = hist2.history['accuracy']
te2 = hist2.history['val_accuracy']
tr3 = hist3.history['accuracy']
te3 = hist3.history['val_accuracy']
tr4 = hist4.history['accuracy']
te4 = hist4.history['val_accuracy']
tr5 = hist5.history['accuracy']
te5 = hist5.history['val_accuracy']
tr6 = hist6.history['accuracy']
te6 = hist6.history['val_accuracy']
tr7 = hist7.history['accuracy']
te7 = hist7.history['val_accuracy']
tr8 = hist8.history['accuracy']
te8 = hist8.history['val_accuracy']
tr9 = hist9.history['accuracy']
te9 = hist9.history['val_accuracy']
tr10 = hist10.history['accuracy']
te10 = hist10.history['val_accuracy']
tr11 = hist11.history['accuracy']
te11 = hist11.history['val_accuracy']
tr12 = hist12.history['accuracy']
te12 = hist12.history['val_accuracy']
tr13 = hist13.history['accuracy']
te13 = hist13.history['val_accuracy']
tr14 = hist14.history['accuracy']
te14 = hist14.history['val_accuracy']
tr15 = hist15.history['accuracy']
te15 = hist15.history['val_accuracy']
tr16 = hist16.history['accuracy']
te16 = hist16.history['val_accuracy']
# Specify the filename
filename = "S&P500_ReN_history.trial6.csv"

# Write to the CSV file
with open(filename, mode='w', newline='') as file:
    writer = csv.writer(file)
    
    # Write the header
    writer.writerow(['tr1', 'te1', 'tr2', 'te2', 'tr3', 'te3', 'tr4', 'te4', 'tr5', 'te5', 'tr6', 'te6', 'tr7', 'te7', 'tr8', 'te8', 'tr9', 'te9', 'tr10', 'te10', 'tr11', 'te11', 'tr12', 'te12', 'tr13', 'te13', 'tr14', 'te14', 'tr15', 'te15', 'tr16', 'te16'])
    
    # Write the data rows
    for a1,b1,a2,b2,a3,b3,a4,b4,a5,b5,a6,b6,a7,b7,a8,b8,a9,b9,a10,b10,a11,b11,a12,b12,a13,b13,a14,b14,a15,b15,a16,b16 in zip(tr1, te1, tr2, te2, tr3, te3, tr4, te4, tr5, te5, tr6, te6,
tr7, te7, tr8, te8, tr9, te9, tr10, te10, tr11, te11, tr12, te12,
tr13, te13, tr14, te14, tr15, te15, tr16, te16):
        writer.writerow([a1,b1,a2,b2,a3,b3,a4,b4,a5,b5,a6,b6,a7,b7,a8,b8,a9,b9,a10,b10,a11,b11,a12,b12,a13,b13,a14,b14,a15,b15,a16,b16])

print(f"Data successfully written to {filename}")

Data successfully written to S&P500_ReN_history.trial6.csv


In [23]:
series = []
for i in range(1, 17):
    series.append(f"tr{i}")
    series.append(f"te{i}")

print(series)

['tr1', 'te1', 'tr2', 'te2', 'tr3', 'te3', 'tr4', 'te4', 'tr5', 'te5', 'tr6', 'te6', 'tr7', 'te7', 'tr8', 'te8', 'tr9', 'te9', 'tr10', 'te10', 'tr11', 'te11', 'tr12', 'te12', 'tr13', 'te13', 'tr14', 'te14', 'tr15', 'te15', 'tr16', 'te16']


In [24]:
series = []
for i in range(1, 17):
    series.append(f"tr{i}")
    series.append(f"te{i}")

print(series)

['tr1', 'te1', 'tr2', 'te2', 'tr3', 'te3', 'tr4', 'te4', 'tr5', 'te5', 'tr6', 'te6', 'tr7', 'te7', 'tr8', 'te8', 'tr9', 'te9', 'tr10', 'te10', 'tr11', 'te11', 'tr12', 'te12', 'tr13', 'te13', 'tr14', 'te14', 'tr15', 'te15', 'tr16', 'te16']


In [25]:
series = []
for i in range(1, 17):
    series.append(f"a{i}")
    series.append(f"b{i}")

print(series)

text = series
cleaned_text = ' '.join(text.split())
print(cleaned_text)

['a1', 'b1', 'a2', 'b2', 'a3', 'b3', 'a4', 'b4', 'a5', 'b5', 'a6', 'b6', 'a7', 'b7', 'a8', 'b8', 'a9', 'b9', 'a10', 'b10', 'a11', 'b11', 'a12', 'b12', 'a13', 'b13', 'a14', 'b14', 'a15', 'b15', 'a16', 'b16']


AttributeError: 'list' object has no attribute 'split'